In [41]:
import time
import json
from concurrent.futures import ThreadPoolExecutor, as_completed
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import NoSuchElementException, TimeoutException
from selenium.webdriver.chrome.options import Options
import os

from dotenv import load_dotenv
load_dotenv()

options = Options()
options.add_argument("--disable-gpu")
options.add_argument("--disable-software-rasterizer")

# LinkedIn Credentials
username = os.getenv("username_linkedin")
password = os.getenv("password_linkedin")
print(username,password)
# Initialize drivers
drivers = webdriver.Chrome()

DEBUG:selenium.webdriver.common.selenium_manager:Selenium Manager binary found at: c:\Users\AbhishekNanda\Documents\AI_Agent-Compitator-Analysis\env\Lib\site-packages\selenium\webdriver\common\windows\selenium-manager.exe
DEBUG:selenium.webdriver.common.selenium_manager:Executing process: c:\Users\AbhishekNanda\Documents\AI_Agent-Compitator-Analysis\env\Lib\site-packages\selenium\webdriver\common\windows\selenium-manager.exe --browser chrome --debug --language-binding python --output json


None None


DEBUG:selenium.webdriver.common.selenium_manager:Sending stats to Plausible: Props { browser: "chrome", browser_version: "", os: "windows", arch: "x86_64", lang: "python", selenium_version: "4.35" }
DEBUG:selenium.webdriver.common.selenium_manager:chromedriver not found in PATH
DEBUG:selenium.webdriver.common.selenium_manager:chrome detected at C:\Program Files\Google\Chrome\Application\chrome.exe
DEBUG:selenium.webdriver.common.selenium_manager:Detected browser: chrome 140.0.7339.128
DEBUG:selenium.webdriver.common.selenium_manager:Discovering versions from https://googlechromelabs.github.io/chrome-for-testing/known-good-versions-with-downloads.json
DEBUG:selenium.webdriver.common.selenium_manager:Required driver: chromedriver 140.0.7339.185
DEBUG:selenium.webdriver.common.selenium_manager:chromedriver 140.0.7339.185 already in the cache
DEBUG:selenium.webdriver.common.selenium_manager:Driver path: C:\Users\AbhishekNanda\.cache\selenium\chromedriver\win64\140.0.7339.185\chromedriver.e

In [42]:
from dotenv import load_dotenv
load_dotenv()


username = os.getenv("LINKEDIN_USER")
password = os.getenv("LINKEDIN_PASS")
openai_key = os.getenv("OPENAI_API_KEY")

In [43]:
def login(driver, username, password):
    """Logs in to LinkedIn with the specified driver."""
    driver.get("https://www.linkedin.com/login")
    WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.ID, "username"))).send_keys(username)
    driver.find_element(By.ID, "password").send_keys(password)
    driver.find_element(By.XPATH, '//button[@type="submit"]').click()
    time.sleep(3)  # Wait for login to complete

login(drivers, username, password)


DEBUG:selenium.webdriver.remote.remote_connection:POST http://localhost:58740/session/9d5352700a64aa3396bab246012c5a4f/url {'url': 'https://www.linkedin.com/login'}
DEBUG:urllib3.connectionpool:http://localhost:58740 "POST /session/9d5352700a64aa3396bab246012c5a4f/url HTTP/1.1" 200 0
DEBUG:selenium.webdriver.remote.remote_connection:Remote response: status=200 | data={"value":null} | headers=HTTPHeaderDict({'Content-Length': '14', 'Content-Type': 'application/json; charset=utf-8', 'cache-control': 'no-cache'})
DEBUG:selenium.webdriver.remote.remote_connection:Finished Request
DEBUG:selenium.webdriver.remote.remote_connection:POST http://localhost:58740/session/9d5352700a64aa3396bab246012c5a4f/element {'using': 'css selector', 'value': '[id="username"]'}
DEBUG:urllib3.connectionpool:http://localhost:58740 "POST /session/9d5352700a64aa3396bab246012c5a4f/element HTTP/1.1" 200 0
DEBUG:selenium.webdriver.remote.remote_connection:Remote response: status=200 | data={"value":{"element-6066-11e

In [14]:
company_names = "Udacity"
drivers.get(f"https://www.linkedin.com/company/{company_names}/posts/")

Linkdin crawler without AI

In [15]:
## Linkedin crawler without AI

In [15]:
import time
import json
import re
from datetime import datetime, timedelta
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import (
    StaleElementReferenceException, NoSuchElementException, WebDriverException, TimeoutException
)

# ---------- helpers ----------
def _safe_text(el):
    try:
        return el.text.strip()
    except Exception:
        try:
            return el.get_attribute("textContent").strip()
        except Exception:
            return ""

def _find_anchor_href_in_el(el, pattern=None):
    try:
        anchors = el.find_elements(By.CSS_SELECTOR, "a[href]")
    except Exception:
        return None
    for a in anchors:
        try:
            href = a.get_attribute("href") or ""
            if not href or href.startswith("javascript:"):
                continue
            if pattern:
                if re.search(pattern, href):
                    return href
            else:
                if href.startswith("http"):
                    return href
        except StaleElementReferenceException:
            continue
    return None

def _get_post_permalink(el, driver):
    """
    Best-effort permalink:
      - data-urn if present
      - anchor inside post pointing to feed/update, activity or posts
      - time element ancestor anchor fallback
    """
    try:
        # 1) data-urn attributes
        data_urn = None
        try:
            data_urn = el.get_attribute("data-urn") or el.get_attribute("data-entity-urn") or el.get_attribute("data-urn-activity")
        except Exception:
            data_urn = None
        if data_urn and "urn:li:activity:" in data_urn:
            return f"https://www.linkedin.com/feed/update/{data_urn}/"

        # 2) anchors inside the post
        href = _find_anchor_href_in_el(el, r"/feed/update/urn:li:activity:|/activity:|/posts/|/feed/update/")
        if href:
            if href.startswith("/"):
                return "https://www.linkedin.com" + href
            return href

        # 3) look at time element and find parent <a>
        try:
            time_el = el.find_element(By.CSS_SELECTOR, "time")
            script = (
                "let node = arguments[0]; "
                "while(node){ if(node.tagName==='A' && node.href) return node.href; node = node.parentElement; }"
                "return null;"
            )
            href = driver.execute_script(script, time_el)
            if href:
                return href
        except Exception:
            pass

        # 4) fallback: any feed/update anchor anywhere in element
        href = _find_anchor_href_in_el(el, r"/feed/update/|/posts/|/activity/")
        if href:
            return href if href.startswith("http") else "https://www.linkedin.com" + href

    except StaleElementReferenceException:
        return None
    except Exception:
        return None

    return None

def _parse_int_from_text(txt):
    if not txt:
        return 0
    # remove commas, non-digit prefixes/suffixes
    # sometimes '3,493 reactions' or '71 comments' etc.
    m = re.search(r'([\d,]+)', txt.replace('\xa0', ' '))
    if m:
        return int(m.group(1).replace(',', ''))
    try:
        return int(txt)
    except Exception:
        return 0

# ---------- click helpers ----------
def _click_element(driver, el):
    try:
        el.click()
        return True
    except Exception:
        try:
            driver.execute_script("arguments[0].click();", el)
            return True
        except Exception:
            return False

def _click_while_present(driver, el, selector_css, max_clicks=10, small_wait=0.25):
    clicks = 0
    while clicks < max_clicks:
        try:
            buttons = el.find_elements(By.CSS_SELECTOR, selector_css)
        except Exception:
            break
        if not buttons:
            break
        any_clicked = False
        for b in buttons:
            try:
                if not b.is_displayed():
                    continue
                if _click_element(driver, b):
                    any_clicked = True
                    clicks += 1
                    time.sleep(small_wait)
                    if clicks >= max_clicks:
                        break
            except StaleElementReferenceException:
                continue
        if not any_clicked:
            break

# ---------- comment / thread extraction ----------
def _extract_comment_node_data(comment_el, driver):
    """
    Extract a single comment node.
    Returns dict or None on failure.
    """
    try:
        # comment id
        comment_id = None
        try:
            data_id = comment_el.get_attribute("data-id") or comment_el.get_attribute("data-comment-id")
            if data_id:
                comment_id = data_id
        except Exception:
            comment_id = None

        # author name & profile
        author = ""
        author_profile = None
        try:
            a = comment_el.find_element(By.CSS_SELECTOR, "a.comments-comment-meta__image-link, a.comments-comment-meta__description-container, a[href*='/in/'], a[href*='/profile/view'], a[href*='/company/']")
            author = (a.text or a.get_attribute("textContent") or "").strip()
            author_profile = a.get_attribute("href")
        except Exception:
            # fallback: title span
            try:
                author = _safe_text(comment_el.find_element(By.CSS_SELECTOR, ".comments-comment-meta__description-title, .feed-shared-actor__name"))
            except Exception:
                author = _safe_text(comment_el)

        # raw_time
        raw_time = ""
        try:
            t = comment_el.find_element(By.CSS_SELECTOR, "time, .comments-comment-meta__data")
            raw_time = t.get_attribute("datetime") or t.text or ""
        except Exception:
            raw_time = ""

        # text content
        text = ""
        try:
            # common selectors
            candidates = [".comments-comment-item__main-content .update-components-text", ".comments-comment-item__main-content", ".feed-shared-inline-show-more-text .update-components-text", ".update-components-text", ".feed-shared-text"]
            for sel in candidates:
                try:
                    node = comment_el.find_element(By.CSS_SELECTOR, sel)
                    text = driver.execute_script("return arguments[0].textContent", node) or node.text
                    text = (text or "").strip()
                    if text:
                        break
                except Exception:
                    continue
            if not text:
                text = _safe_text(comment_el)
        except Exception:
            text = _safe_text(comment_el)

        # comment-level reaction count (if shown)
        comment_reactions = 0
        try:
            # buttons with classes like comments-comment-social-bar__reactions-count--cr
            btn = comment_el.find_element(By.CSS_SELECTOR, "button.comments-comment-social-bar__reactions-count--cr, button.comments-comment-social-bar__count, .comments-comment-social-bar__reactions-count--cr")
            if btn:
                comment_reactions = _parse_int_from_text(btn.text)
        except Exception:
            # sometimes there's a separate count span/button near the social bar
            try:
                btn2 = comment_el.find_element(By.XPATH, ".//button[contains(@aria-label,'Reaction') or contains(@aria-label,'Reactions') or contains(@aria-label,'reaction')]")
                comment_reactions = _parse_int_from_text(btn2.text)
            except Exception:
                comment_reactions = 0

        # replies: find nested reply containers and parse
        replies = []
        try:
            reply_containers = comment_el.find_elements(By.CSS_SELECTOR, "div.comments-replies-list, div.comments-comment-replies, ul.comment-replies, div.comments-thread-entity")
            for rc in reply_containers:
                try:
                    # find all reply articles inside container
                    items = rc.find_elements(By.CSS_SELECTOR, "article.comments-comment-entity, li.comments-comment-entity, div.comments-comment-entity")
                    for it in items:
                        try:
                            # avoid re-parsing parent comment if structure overlaps
                            if it == comment_el:
                                continue
                            rdata = _extract_comment_node_data(it, driver)
                            if rdata:
                                replies.append(rdata)
                        except Exception:
                            continue
                except Exception:
                    continue
        except Exception:
            replies = []

        return {
            "comment_id": comment_id,
            "author": author,
            "author_profile": author_profile,
            "text": text,
            "raw_time": raw_time,
            "reactions": comment_reactions,
            "replies": replies
        }
    except StaleElementReferenceException:
        return None
    except Exception:
        return None

def _collect_all_comments_for_post(el, driver, max_expand_clicks=20, reply_expand_clicks=30, per_post_timeout=25):
    """
    Open comments UI, expand comments/replies, and parse threaded comments.
    """
    start = time.time()
    # scroll post into view first
    try:
        driver.execute_script("arguments[0].scrollIntoView({block:'center'});", el)
        time.sleep(0.12)
    except Exception:
        pass

    # Attempt to click the Comment button to open the comment container
    try:
        # common comment button selectors inside a post
        comment_btn_selectors = [
            "button[aria-label*='Comment']",
            "button.comment-button",
            "button[data-control-name='comment']",
            "button[aria-label^='Comment']"
        ]
        opened = False
        for sel in comment_btn_selectors:
            try:
                btns = el.find_elements(By.CSS_SELECTOR, sel)
                for b in btns:
                    try:
                        if not b.is_displayed():
                            continue
                        _click_element(driver, b)
                        opened = True
                        time.sleep(0.35)
                        break
                    except Exception:
                        continue
                if opened:
                    break
            except Exception:
                continue
    except Exception:
        pass

    # allow comment container to render
    time.sleep(0.25)

    # Expand "Load more comments" inside the post
    comment_load_selectors = [
        "button.comments-comments-list__load-more-comments-button",
        "button.comments-comments-list__load-more-comments-button--cr",
        "button.comments-comments-list__load-more-comments-button, button.comments-comments-list__load-more-comments-button--cr",
        "button.comments-comments-list__load-more-comments-button--cr, button.comments-comments-list__load-more-comments-button",
        "button.comments-comments-list__load-more-comments-button, button.comments-comments-list__load-more-comments-arrows, button.comments-comments-list__load-more-comments-button--cr",
        "button.comments-comments-list__load-more-comments-button--cr",
        "button.comments-comments-list__load-more-comments-button",
        "button.comments-comments-list__load-more-comments-button, button.comments-comments-list__load-more-comments" ,
        "button.comments-comments-list__load-more-comments-button--cr, button.comments-comments-list__load-more-comments-button"
    ]
    for sel in comment_load_selectors:
        if (time.time() - start) > per_post_timeout:
            break
        _click_while_present(driver, el, sel, max_clicks=max_expand_clicks, small_wait=0.25)

    # Expand replies
    reply_load_selectors = [
        "button.comment-replies__load-more, button.comments-replies-load-more__button, button.comments-replies__load-more",
        "button[data-control-name='load_more_replies']",
        "button[aria-label*='replies']",
        "button[aria-label*='replies'], button[aria-label*='reply']"
    ]
    for sel in reply_load_selectors:
        if (time.time() - start) > per_post_timeout:
            break
        _click_while_present(driver, el, sel, max_clicks=reply_expand_clicks, small_wait=0.2)

    # optionally, set comments sort to Most recent
    try:
        # Find the sort toggle inside the post's comments container
        try:
            sort_trigger = el.find_element(By.CSS_SELECTOR, "button.comments-sort-order-toggle__trigger, .comments-sort-order-toggle__trigger")
            _click_element(driver, sort_trigger)
            time.sleep(0.15)
            # possible option texts to select
            desired_texts = ["Most recent", "Newest", "Recent", "Most recent (newest)"]
            # find dropdown items
            dropdown_root = None
            try:
                dropdown_root = driver.find_element(By.CSS_SELECTOR, ".comments-sort-order-toggle__content, .dropdown-options.comments-sort-order-toggle__content, div.dropdown-options")
            except Exception:
                pass
            # Try to click by texts inside the open dropdown or globally with XPath (safer)
            clicked_sort = False
            for txt in desired_texts:
                try:
                    # XPath matching element that contains the exact text or contains text
                    opt = None
                    try:
                        opt = driver.find_element(By.XPATH, f"//button[contains(normalize-space(string(.)), '{txt}')]")
                    except Exception:
                        try:
                            opt = driver.find_element(By.XPATH, f"//li[contains(normalize-space(string(.)), '{txt}')]")
                        except Exception:
                            opt = None
                    if opt:
                        _click_element(driver, opt)
                        clicked_sort = True
                        time.sleep(0.15)
                        break
                except Exception:
                    continue
            # close dropdown if still open
            if not clicked_sort:
                try:
                    # click outside
                    driver.execute_script("document.body.click();")
                except Exception:
                    pass
        except Exception:
            pass
    except Exception:
        pass

    # small wait
    time.sleep(0.25)

    # locate comment nodes (many fallbacks)
    comment_nodes = []
    try:
        selectors = [
            "div.comments-comments-list article.comments-comment-entity, div.comments-comment-entity",
            "div.comments-comments-list__container article.comments-comment-entity, div.comments-comment-list__container article.comments-comment-entity",
            "div.comments-comments-list article, article.comments-comment-entity",
            "div.comments-comment-list__container article.comments-comment-entity",
            "div.comments-comments-list article, li.comments-comment-entity"
        ]
        for sel in selectors:
            try:
                found = el.find_elements(By.CSS_SELECTOR, sel)
                if found:
                    comment_nodes = found
                    break
            except Exception:
                continue
    except Exception:
        comment_nodes = []

    comments_data = []
    for cn in comment_nodes:
        if (time.time() - start) > per_post_timeout:
            break
        try:
            data = _extract_comment_node_data(cn, driver)
            if data:
                comments_data.append(data)
        except Exception:
            continue

    return comments_data

# ---------- social counts extraction ----------
def _extract_social_counts(el):
    """
    From social-details-social-counts element inside post extract:
    - reactions_count
    - comments_count
    - reposts_count
    - reaction_type_icons (list of types seen)
    """
    reactions_count = 0
    comments_count = 0
    reposts_count = 0
    reaction_types = []
    try:
        # find the social counts container
        container = None
        try:
            container = el.find_element(By.CSS_SELECTOR, "div.social-details-social-counts, div.social-details-social-counts__item, div.update-v2-social-activity")
        except Exception:
            container = None

        if container:
            # reactions: look for li or button with reactions
            try:
                # try common reaction item
                reaction_item = container.find_element(By.CSS_SELECTOR, "li.social-details-social-counts__reactions, li.social-details-social-counts__item.social-details-social-counts__reactions")
                # count text often inside a span
                try:
                    span = reaction_item.find_element(By.CSS_SELECTOR, "span.social-details-social-counts__reactions-count, span.social-details-social-counts__reactions-count, span")
                    reactions_count = _parse_int_from_text(span.text)
                except Exception:
                    # fallback to button text
                    try:
                        btn = reaction_item.find_element(By.CSS_SELECTOR, "button")
                        reactions_count = _parse_int_from_text(btn.text)
                    except Exception:
                        reactions_count = 0
                # extract reaction-type images if present
                try:
                    imgs = reaction_item.find_elements(By.CSS_SELECTOR, "img[data-test-reactions-icon-type]")
                    for im in imgs:
                        t = im.get_attribute("data-test-reactions-icon-type") or im.get_attribute("alt") or ""
                        if t:
                            reaction_types.append(t)
                except Exception:
                    pass
            except Exception:
                # alternative approach: find any button with 'reactions' aria-label
                try:
                    btn = container.find_element(By.XPATH, ".//button[contains(@aria-label, 'reactions') or contains(@aria-label, 'reaction')]")
                    reactions_count = _parse_int_from_text(btn.text)
                except Exception:
                    reactions_count = 0

            # comments count
            try:
                # find a button (or li) that contains 'comments' text
                comment_btn = container.find_element(By.XPATH, ".//button[contains(translate(., 'COMMENTS', 'comments'), 'comments') or contains(translate(., 'comment', 'comment'), 'comment')]")
                comments_count = _parse_int_from_text(comment_btn.text)
            except Exception:
                # also check for a span with 'comments'
                try:
                    comments_count = 0
                    spans = container.find_elements(By.XPATH, ".//span[contains(., 'comments') or contains(., 'comment')]")
                    for s in spans:
                        if re.search(r'\d', s.text or ""):
                            comments_count = _parse_int_from_text(s.text)
                            break
                except Exception:
                    comments_count = 0

            # reposts count
            try:
                repost_btn = container.find_element(By.XPATH, ".//button[contains(translate(., 'REPOSTS', 'reposts'), 'reposts') or contains(., 'repost')]")
                reposts_count = _parse_int_from_text(repost_btn.text)
            except Exception:
                # fallback: look for li with 'repost' word
                try:
                    repost_span = container.find_element(By.XPATH, ".//span[contains(., 'repost') or contains(., 'reposts')]")
                    reposts_count = _parse_int_from_text(repost_span.text)
                except Exception:
                    reposts_count = 0

    except Exception:
        reactions_count = comments_count = reposts_count = 0
    return {
        "reactions_count": reactions_count,
        "comments_count": comments_count,
        "reposts_count": reposts_count,
        "reaction_types": list(dict.fromkeys(reaction_types))
    }

# ---------- main integrator ----------
def scrape_posts_with_comments(driver,
                               post_selector="div.occludable-update, div.feed-shared-update-v2, div[data-urn^='urn:li:activity']",
                               scroll_times=4,
                               scroll_pause=0.6,
                               days=30,
                               max_posts=None,
                               save_json="linkedin_posts_with_threads_and_counts.json"):
    """
    Scans posts on the current page, extracts permalinks, text, media, social counts,
    and threaded comments (expanded & sorted to Most recent when possible).
    """
    cutoff = datetime.now() - timedelta(days=days)
    results = []
    seen = set()

    # initial scroll to load content
    for _ in range(scroll_times):
        try:
            driver.execute_script("window.scrollBy(0, Math.max(document.documentElement.clientHeight, 800));")
            time.sleep(scroll_pause)
        except Exception:
            break

    # find post elements
    try:
        post_elems = driver.find_elements(By.CSS_SELECTOR, post_selector)
    except Exception:
        post_elems = []

    for el in post_elems:
        if max_posts and len(results) >= max_posts:
            break
        try:
            # generate uid to avoid duplicates
            uid = el.get_attribute("data-urn") or el.get_attribute("id") or (el.get_attribute("data-entity-urn") or "") or (_safe_text(el)[:200])
            if not uid:
                uid = str(hash(_safe_text(el)[:400]))
            if uid in seen:
                continue
            seen.add(uid)

            # permalink
            permalink = _get_post_permalink(el, driver)
            if not permalink:
                href = _find_anchor_href_in_el(el, r"/feed/update/urn:li:activity:|/feed/update/|/posts/|/activity/")
                if href:
                    permalink = href if href.startswith("http") else "https://www.linkedin.com" + href

            # extract main text
            text = ""
            try:
                candidates = ["div.update-components-text, div.feed-shared-update-v2__description, div.feed-shared-text, span.break-words"]
                txt_el = None
                for sel in ["div.update-components-text", "div.feed-shared-update-v2__description", "div.feed-shared-text", "span.break-words", "div.update-components-update-v2__commentary"]:
                    try:
                        txt_el = el.find_element(By.CSS_SELECTOR, sel)
                        if txt_el:
                            text = driver.execute_script("return arguments[0].textContent", txt_el) or txt_el.text or ""
                            text = (text or "").strip()
                            if text:
                                break
                    except Exception:
                        continue
                if not text:
                    text = _safe_text(el)
            except Exception:
                text = _safe_text(el)

            # raw_time
            raw_time = ""
            try:
                t = el.find_element(By.CSS_SELECTOR, "time, .update-components-actor__sub-description")
                raw_time = t.get_attribute("datetime") or t.text or ""
            except Exception:
                raw_time = ""

            # images
            images = []
            try:
                imgs = el.find_elements(By.CSS_SELECTOR, "img")
                for im in imgs:
                    try:
                        v = im.get_attribute("src") or im.get_attribute("data-src") or im.get_attribute("data-delayed-url") or ""
                        if v and not v.startswith("data:"):
                            if "," in v:
                                v = v.split(",")[0].split()[0]
                            images.append(v)
                    except Exception:
                        continue
            except Exception:
                images = []

            # videos / iframes
            videos = []
            try:
                vids = el.find_elements(By.CSS_SELECTOR, "video, iframe")
                for v in vids:
                    try:
                        vs = v.get_attribute("src") or v.get_attribute("data-src") or ""
                        if vs:
                            videos.append(vs)
                    except Exception:
                        continue
            except Exception:
                videos = []

            # social counts (likes/comments/reposts)
            social_counts = _extract_social_counts(el)

            # collect comments_thread (attempt)
            comments_thread = []
            try:
                comments_thread = _collect_all_comments_for_post(el, driver,
                                                                max_expand_clicks=12,
                                                                reply_expand_clicks=40,
                                                                per_post_timeout=30)
            except Exception:
                comments_thread = []

            post_obj = {
                "uid": uid,
                "permalink": permalink,
                "post_url": permalink,  # backward compat
                "text": text,
                "raw_time": raw_time,
                "images": list(dict.fromkeys(images)),
                "videos": list(dict.fromkeys(videos)),
                "social_counts": social_counts,
                "comments_thread": comments_thread
            }
            results.append(post_obj)

        except StaleElementReferenceException:
            continue
        except Exception:
            continue

    # save results
    try:
        with open(save_json, "w", encoding="utf-8") as fh:
            json.dump(results, fh, ensure_ascii=False, indent=2)
        print(f"Saved {len(results)} posts to {save_json}")
    except Exception as e:
        print("Failed to save JSON:", e)

    return results

# -------------------------
# Example usage (you must create and login driver before calling):
#
# from selenium import webdriver
# driver = webdriver.Chrome(...)
# driver.get("https://www.linkedin.com/company/udacity/posts/")
# # ensure logged in and page is loaded
# posts = scrape_posts_with_comments(driver, max_posts=20, days=90)
#
# -------------------------


In [16]:
posts = scrape_posts_with_comments(drivers, max_posts=20, days=7)

Saved 3 posts to linkedin_posts_with_threads_and_counts.json


In [16]:
## Linkedin crawler with AI

In [55]:
# linkedin_scraper_with_sentiment.py
import os
import time
import json
import re
from datetime import datetime, timedelta,timezone
from typing import Optional, List, Dict, Any, Tuple
import logging
from pydantic import BaseModel, Field, ValidationError



OUTPUT_FILENAME = "processed_linkedin_posts.json"

logger = logging.getLogger(__name__)
logging.basicConfig(level=logging.DEBUG)  # change to INFO in production

from selenium.webdriver.common.by import By
from selenium.common.exceptions import (
    StaleElementReferenceException, NoSuchElementException, WebDriverException
)

# OpenAI
from openai import OpenAI

# pydantic v2
from pydantic import BaseModel, Field, ValidationError

# ---------- helpers ----------

def _safe_text(el):
    try:
        return el.text.strip()
    except Exception:
        try:
            return el.get_attribute("textContent").strip()
        except Exception:
            return ""

def _find_anchor_href_in_el(el, pattern=None):
    """Return first href from anchors inside el that matches pattern (regex string) or first absolute href."""
    try:
        anchors = el.find_elements(By.CSS_SELECTOR, "a[href]")
    except Exception:
        return None
    for a in anchors:
        try:
            href = a.get_attribute("href") or ""
            if not href or href.startswith("javascript:"):
                continue
            if pattern:
                if re.search(pattern, href):
                    return href
            else:
                if href.startswith("http"):
                    return href
        except StaleElementReferenceException:
            continue
    return None

def _unique_preserve_order(seq):
    seen = set()
    out = []
    for s in seq:
        if not s or s in seen:
            continue
        seen.add(s)
        out.append(s)
    return out

def _get_post_permalink(el, driver, company_base_url=None):
    """
    Best-effort permalink:
      1) data-urn attribute if 'urn:li:activity:...' -> build /feed/update/{urn}/
      2) find anchor with '/feed/update/urn:li:activity:' or '/activity/' or '/posts/'
      3) find time element and walk up ancestors to find an <a href> (timestamp often links to permalink)
      4) fallback: any feed/update link found in attachments
      5) fallback: build using company_base_url + # + data-urn or element id
    """
    try:
        # 1) data-urn
        data_urn = None
        try:
            data_urn = el.get_attribute("data-urn") or el.get_attribute("data-entity-urn") or None
        except Exception:
            data_urn = None
        if data_urn and "urn:li:activity:" in data_urn:
            return f"https://www.linkedin.com/feed/update/{data_urn}/"

        # 2) look for specific anchors inside post
        href = _find_anchor_href_in_el(el, r"/feed/update/urn:li:activity:|/activity/|/posts/|/feed/update/")
        if href:
            if href.startswith("/"):
                return "https://www.linkedin.com" + href
            return href

        # 3) find time element and ascend to nearest anchor (timestamp often links to the post)
        try:
            time_el = el.find_element(By.CSS_SELECTOR, "time")
            script = (
                "let node = arguments[0]; "
                "while(node){ if(node.tagName==='A' && node.href) return node.href; node = node.parentElement; }"
                "return null;"
            )
            href = driver.execute_script(script, time_el)
            if href:
                return href
        except Exception:
            pass

        # 4) fallback: search attachments/anchors text for feed/update pattern
        href = _find_anchor_href_in_el(el, r"/feed/update/urn:li:activity:|/feed/update/")
        if href:
            return href if href.startswith("http") else "https://www.linkedin.com" + href

        # 5) fallback: build synthetic permalink if company_base_url and data_urn or id available
        eid = el.get_attribute("id") or ""
        if data_urn:
            return f"{company_base_url or 'https://www.linkedin.com'}/feed/update/{data_urn}/"
        if eid:
            return f"{company_base_url or 'https://www.linkedin.com'}/posts/{eid}"

    except StaleElementReferenceException:
        return None
    except Exception:
        return None

    return None

# ---------- comment / thread extraction ----------

def _click_while_present(driver, el, selector_css, max_clicks=10, small_wait=0.2):
    clicks = 0
    while clicks < max_clicks:
        try:
            buttons = el.find_elements(By.CSS_SELECTOR, selector_css)
        except Exception:
            break
        if not buttons:
            break
        any_clicked = False
        for b in buttons:
            try:
                if not b.is_displayed():
                    continue
                try:
                    b.click()
                except Exception:
                    try:
                        driver.execute_script("arguments[0].click();", b)
                    except Exception:
                        continue
                any_clicked = True
                clicks += 1
                time.sleep(small_wait)
                if clicks >= max_clicks:
                    break
            except StaleElementReferenceException:
                continue
        if not any_clicked:
            break

def _extract_comment_node_data(comment_el, driver):
    """
    Extract a single comment node: author, author_profile, text, raw_time, replies (list), reactions (count)
    """
    try:
        author = ""
        author_profile = None
        try:
            a = comment_el.find_element(By.CSS_SELECTOR, "a[href*='/in/'], a.comments-comment-meta__description-container, a.comments-comment-meta__image-link")
            author = (a.text or a.get_attribute("textContent") or "").strip()
            author_profile = a.get_attribute("href")
        except Exception:
            try:
                author = _safe_text(comment_el.find_element(By.CSS_SELECTOR, ".comments-comment-meta__description-title"))
            except Exception:
                author = ""

        raw_time = ""
        try:
            t = comment_el.find_element(By.CSS_SELECTOR, "time, .comments-comment-meta__data")
            raw_time = t.get_attribute("datetime") or t.text or ""
        except Exception:
            try:
                spans = comment_el.find_elements(By.CSS_SELECTOR, "span")
                for s in spans:
                    txt = (s.text or "").strip()
                    if re.search(r'\b(ago|h|hour|d|day|mo|month|[0-9]{4}-[0-9]{2}-[0-9]{2})\b', txt, flags=re.I):
                        raw_time = txt
                        break
            except Exception:
                raw_time = ""

        # comment text
        text = ""
        try:
            candidates = [
                ".comments-comment-item__main-content .update-components-text",
                ".comments-comment-item__main-content",
                ".feed-shared-inline-show-more-text .update-components-text",
                ".update-components-text",
                ".feed-shared-text"
            ]
            for sel in candidates:
                try:
                    n = comment_el.find_element(By.CSS_SELECTOR, sel)
                    text = driver.execute_script("return arguments[0].textContent", n) or n.text
                    text = (text or "").strip()
                    if text:
                        break
                except Exception:
                    continue
            if not text:
                text = _safe_text(comment_el)
        except Exception:
            text = _safe_text(comment_el)

        # reactions on comment (if present)
        reactions = None
        try:
            rc_btn = comment_el.find_element(By.CSS_SELECTOR, ".comments-comment-social-bar__reactions-count--cr, .comments-comment-social-bar__reactions-count--cr, button[aria-label*='Reactions'], .comments-comment-social-bar__reactions-count--cr")
            # try to parse number
            txt = (rc_btn.text or rc_btn.get_attribute("textContent") or "").strip()
            m = re.search(r'(\d{1,6})', txt.replace(',', ''))
            if m:
                reactions = m.group(1)
        except Exception:
            reactions = None

        # replies
        replies = []
        try:
            # reply container could be .comments-replies-list or nested article elements with data-id
            reply_containers = comment_el.find_elements(By.CSS_SELECTOR, "div.comments-replies-list, div.comments-replies-list__container, div.comments-replies-list, div.comments-replies")
            for rc in reply_containers:
                try:
                    items = rc.find_elements(By.CSS_SELECTOR, "article.comments-comment-entity, article.comments-comment-entity--reply, div.comments-comment-entity")
                    for ri in items:
                        try:
                            rdata = _extract_comment_node_data(ri, driver)
                            if rdata:
                                replies.append(rdata)
                        except Exception:
                            continue
                except Exception:
                    continue

            # fallback: child articles with reply class
            if not replies:
                items = comment_el.find_elements(By.CSS_SELECTOR, "article.comments-comment-entity--reply, article.comments-comment-entity")
                for ri in items:
                    try:
                        # avoid the top-level comment which may be included
                        if ri == comment_el:
                            continue
                        rdata = _extract_comment_node_data(ri, driver)
                        if rdata:
                            replies.append(rdata)
                    except Exception:
                        continue
        except Exception:
            replies = []

        return {
            "author": author,
            "author_profile": author_profile,
            "text": text,
            "raw_time": raw_time,
            "replies": replies,
            "reactions": reactions
        }
    except StaleElementReferenceException:
        return None
    except Exception:
        return None

def _collect_all_comments_for_post(el, driver, max_expand_clicks=20, reply_expand_clicks=30, per_post_timeout=25):
    """
    Expand comments and replies then parse all comment nodes into threaded structure.
    """
    start = time.time()
    try:
        driver.execute_script("arguments[0].scrollIntoView({block:'center'});", el)
        time.sleep(0.12)
    except Exception:
        pass

    # click load more comments
    comment_load_selectors = [
        "button.comments-comments-list__load-more-comments-button",
        "button.comments-load-more-button",
        "button[jsaction*='loadMoreComments']",
        "button[aria-label*='more comments']",
        "button[aria-label*='comments']",
        "button.comments-comments-list__load-more-comments-button--cr",
        "button.comments-comments-list__load-more-comments-button"
    ]
    for sel in comment_load_selectors:
        if (time.time() - start) > per_post_timeout:
            break
        _click_while_present(driver, el, sel, max_clicks=max_expand_clicks, small_wait=0.25)

    # click load more replies
    reply_load_selectors = [
        "button.comment-replies__load-more, button.comments-replies-load-more__button",
        "button[aria-label*='more replies']",
        "button[data-control-name='load_more_replies']",
        "button.comments-comments-list__load-more-comments-button--cr"
    ]
    for sel in reply_load_selectors:
        if (time.time() - start) > per_post_timeout:
            break
        _click_while_present(driver, el, sel, max_clicks=reply_expand_clicks, small_wait=0.2)

    time.sleep(0.3)

    comment_nodes = []
    try:
        selectors = [
            "ul.comments-comments-list > li, div.comments-comment-item, div.comment, li.comments-comment-item, article.comments-comment-entity",
            "div.update-comments-list__comments-container li, li.comment",
            "div.comments-comment-item, li.comments-comment-item"
        ]
        for sel in selectors:
            try:
                found = el.find_elements(By.CSS_SELECTOR, sel)
                if found:
                    comment_nodes = found
                    break
            except Exception:
                continue
    except Exception:
        comment_nodes = []

    comments_data = []
    for cn in comment_nodes:
        if (time.time() - start) > per_post_timeout:
            break
        try:
            data = _extract_comment_node_data(cn, driver)
            if data:
                comments_data.append(data)
        except Exception:
            continue

    return comments_data

# ---------- OpenAI sentiment analysis integration ----------

class SentimentResponseModel(BaseModel):
    label: str = Field(..., description="one of: positive/neutral/negative")
    score: float = Field(..., ge=0.0, le=1.0, description="normalized confidence score 0..1")
    explanation: Optional[str] = Field(None, description="brief explanation for the label")

class AlertResponseModel(BaseModel):
    title: str = Field(..., description="Title of the alert in 10 words or less")
    message: str = Field(..., description="Detailed message of the alert")
    severity: str = Field(..., description="Severity level of the alert (low|medium|high)")

class LLMAlertRawModel(BaseModel):
    """
    Expected raw LLM response shape. We ask the LLM to return exactly this JSON.
    """
    is_alert: bool
    confidence: float
    reason: str
    suggested_title: Optional[str] = None
    suggested_message: Optional[str] = None
    suggested_severity: Optional[str] = None

# process_linkedin_data_with_alerts.py

def _parse_posted_at(raw_time: Optional[str]) -> str:
    """
    Try several heuristics to parse a 'raw_time' field from LinkedIn.
    If parsing fails or raw_time is None/empty, return current UTC ISO timestamp.
    """
    if not raw_time:
        return datetime.now(timezone.utc).isoformat()

    # common patterns: "1d • \n 1 day ago • Visible..." or "7h" or "1 day ago"
    s = raw_time.strip()
    # look for patterns like 'YYYY-MM-DD' or ISO (unlikely), else numeric + 'd'/'h'/'m'
    iso_match = re.search(r"\d{4}-\d{2}-\d{2}", s)
    if iso_match:
        try:
            return datetime.fromisoformat(iso_match.group(0)).replace(tzinfo=timezone.utc).isoformat()
        except Exception:
            pass

    # relative times like "7h", "1d", "1 day ago", "1 hour ago"
    rel_match = re.search(r"(\d+)\s*(d|day|days|h|hour|hours|m|minute|minutes)\b", s, flags=re.I)
    if rel_match:
        qty = int(rel_match.group(1))
        unit = rel_match.group(2).lower()
        now = datetime.now(timezone.utc)
        if unit.startswith("d"):
            dt = now - timedelta(days=qty)
        elif unit.startswith("h"):
            dt = now - timedelta(hours=qty)
        elif unit.startswith("m"):
            dt = now - timedelta(minutes=qty)
        else:
            dt = now
        return dt.isoformat()

    # fallback: return current time
    return datetime.now(timezone.utc).isoformat()

def process_linkedin_data(data) -> None:
    """
    Reads the input JSON (expected to include fields like 'post_sentiment' and 'post_alert')
    and writes a processed file that combines:
      - basic post metadata,
      - sentiment (label/score/explanation),
      - comments summary,
      - alert details (title/message/severity and optional confidence)

    Output schema (per post):
    {
      "uid", "company_id", "post_platform", "post_url", "post_description", "posted_at",
      "likes", "comments_count", "shares",
      "sentiment_label", "sentiment_score", "sentiment_explanation",
      "comments_summary": {...},
      "alert": {
         "title", "message", "severity", "confidence" (optional)
      }
    }
    """
    print(f"Processing {len(data)} posts...",data)
    processed_posts: List[Dict[str, Any]] = []
    company_id_counter = 1  # simple company id for all posts (adjust as needed)

    for post in data:
        # only process items that look like LinkedIn posts (original code checked uid prefix)
        uid = post.get('uid') or ""
        if not isinstance(uid, str) or not uid.startswith('urn:li:activity:'):
            # optionally still process non-standard entries — here we skip to match previous behavior
            continue

        social_counts = post.get('social_counts') or {}
        post_sentiment = post.get('post_sentiment') or {}
        comments_summary = post.get('comments_sentiment_summary') or {}

        # extract alert info if present
        post_alert = post.get('post_alert') or {}
        alert_title = post_alert.get('title')
        alert_message = post_alert.get('message')
        alert_severity = post_alert.get('severity')
        # some LLM outputs may include confidence or score; try common names
        alert_confidence = post_alert.get('confidence') or post_alert.get('score') or post_alert.get('confidence_score')

        # build processed object
        processed_post: Dict[str, Any] = {
            "uid": uid,
            "company_id": company_id_counter,
            "post_platform": "linkedin",
            "post_url": post.get('post_url'),
            "post_description": post.get('text'),
            # try to parse posted time; fall back to now
            "posted_at": _parse_posted_at(post.get('raw_time') or post.get('raw_time_text') or ""),
            "likes": social_counts.get('reactions_count') if social_counts.get('reactions_count') is not None else 0,
            "comments_count": social_counts.get('comments_count') if social_counts.get('comments_count') is not None else 0,
            "shares": social_counts.get('reposts_count') if social_counts.get('reposts_count') is not None else 0,
            # sentiment
            "sentiment_label": post_sentiment.get('label'),
            "sentiment_score": post_sentiment.get('score'),
            "sentiment_explanation": post_sentiment.get('explanation'),
            # comments summary (keep raw structure to allow further processing)
            "comments_summary": {
                "total_comments": comments_summary.get('total_comments'),
                "positive": comments_summary.get('positive'),
                "neutral": comments_summary.get('neutral'),
                "negative": comments_summary.get('negative'),
                "average_score": comments_summary.get('average_score'),
                "error": comments_summary.get('error', "")
            },
            # alert block
            "alert": {
                "title": alert_title or None,
                "message": alert_message or None,
                "severity": alert_severity or None,
                "confidence": float(alert_confidence) if alert_confidence is not None else None
            }
        }

        processed_posts.append(processed_post)

    return processed_posts





def _build_sentiment_prompt(post_text: str, comments: List[Dict[str, Any]]) -> str:
    """
    Compose prompt: include post text and all comments (flattened up to a safe limit).
    Keep it concise but include enough context for LLM to judge sentiment.
    """
    MAX_CHARS = 12000  # adjust as needed
    pieces = []
    pieces.append("You are a sentiment analysis assistant. Given the main post text and its comments (including replies), classify the overall post sentiment as one of: positive, neutral, or negative. Provide a numeric confidence score between 0.0 and 1.0 (higher means more confident), and a short explanation (1-2 sentences).")
    pieces.append("\n\nMain post:\n")
    pieces.append(post_text or "(no text)")

    pieces.append("\n\nComments (most relevant first):\n")
    # flatten comments into lines; include replies inline to help context
    for c in comments:
        # include author-ish and text
        author = c.get("author") or c.get("author_profile") or "anon"
        text = (c.get("text") or "").strip()
        pieces.append(f"- {author}: {text}")
        # include replies
        for r in c.get("replies", [])[:3]:
            ra = r.get("author") or r.get("author_profile") or "anon"
            rt = (r.get("text") or "").strip()
            pieces.append(f"   - reply {ra}: {rt}")

    prompt = "\n".join(pieces)
    if len(prompt) > MAX_CHARS:
        # truncate comments portion
        prompt = prompt[:MAX_CHARS-200] + "\n\n[TRUNCATED]"
    return prompt

def analyze_post_sentiment(openai_client: OpenAI, post_text: str, comments: List[Dict[str, Any]], model: str = "gpt-4o-mini", max_tokens: int = 512, timeout: int = 60) -> Tuple[Dict[str, Any], Optional[str]]:
    """
    Sends a single API call to OpenAI with post_text + comments, expects JSON-like output.
    Uses the chat completions endpoint and then validates with pydantic model.
    Returns (sentiment_dict, error_message).
    """
    prompt = _build_sentiment_prompt(post_text, comments)

    # system + user messages
    system_msg = {
        "role": "system",
        "content": "You are a helpful assistant that MUST return a JSON object exactly matching the schema: {\"label\": \"positive|neutral|negative\", \"score\": float(0..1), \"explanation\": \"short explanation\"}. Do not return anything else."
    }
    user_msg = {
        "role": "user",
        "content": (
            "Analyze the sentiment and return only the JSON object.\n\n"
            f"Input:\n{prompt}\n\n"
            "Remember: respond ONLY with valid JSON with keys label, score, explanation."
        )
    }

    try:
        resp = openai_client.chat.completions.create(
            model=model,
            messages=[system_msg, user_msg],
            max_tokens=max_tokens,
            temperature=0.0
        )
        # get text
        # depending on the client response shape, extract
        out_text = None
        try:
            out_text = resp.choices[0].message["content"]
        except Exception:
            try:
                out_text = resp.choices[0].text
            except Exception:
                out_text = str(resp)

        # try to locate JSON in output (some LLMs wrap in markdown)
        json_text = out_text.strip()
        # strip code fences
        json_text = re.sub(r"^```(?:json)?\n", "", json_text)
        json_text = re.sub(r"\n```$", "", json_text)
        # try to find first {...}
        m = re.search(r"(\{.*\})", json_text, flags=re.S)
        if m:
            json_text = m.group(1)
        # parse JSON
        try:
            parsed = json.loads(json_text)
        except Exception:
            # fallback: attempt to fix common single quotes -> double quotes
            try:
                parsed = json.loads(json_text.replace("'", '"'))
            except Exception:
                # as last resort, build neutral
                return ({"label":"neutral","score":0.0,"explanation":"Failed to parse model response: "+json_text[:200]}, "parse_error")

        # validate with pydantic
        try:
            model_obj = SentimentResponseModel.model_validate(parsed)
            return (model_obj.model_dump(), None)
        except ValidationError as ve:
            # try to coerce values
            try:
                coerced = {
                    "label": parsed.get("label", "neutral"),
                    "score": float(parsed.get("score", 0.0)) if parsed.get("score") is not None else 0.0,
                    "explanation": parsed.get("explanation", "")
                }
                model_obj = SentimentResponseModel.model_validate(coerced)
                return (model_obj.model_dump(), None)
            except Exception as e2:
                return ({"label":"neutral","score":0.0,"explanation":"Validation failed: "+str(ve)}, "validation_error")
    except Exception as oe:
    # optionally check if oe is from the openai library by type or name
        return ({"label":"neutral","score":0.0,"explanation":f"OpenAI API error: {str(oe)}"}, "openai_error")

    except Exception as e:
        return ({"label":"neutral","score":0.0,"explanation":f"Unexpected error: {str(e)}"}, "unexpected_error")


# ----- Prompt builder -----
def _build_alert_prompt(
    post_text: str,
    comments: List[Dict[str, Any]],
    metadata: Optional[Dict[str, Any]] = None,
    max_chars: int = 12000
) -> str:
    """
    Compose the prompt that will be sent to the LLM.
    Uses a detailed competitor-intelligence instruction set.
    """
    pieces = [
    """You are a COMPETITOR INTELLIGENCE classification assistant.

Your job
------
Decide whether a LinkedIn post (including its comments/replies) should trigger a COMPETITOR ALERT for the *target company* (use metadata.target_company when available). A COMPETITOR ALERT means the post contains timely, verifiable, or plausible information that may affect the target company's strategy, product competitiveness, hiring, market share, or reputation.

What to look for (signals)
--------------------------
- Product & Service Launches: new products, betas, feature rollouts, rebrands, or explicit product claims.
- Pricing & Promotions: pricing model changes, large discounts, free tiers, or claims like "40% cheaper".
- Hiring & Talent Moves: large hires, new R&D centers, key exec moves, or targeted recruitment campaigns.
- Partnerships, M&A & Funding: alliances, integrations, acquisitions, funding rounds, or investor news.
- Customer Wins & Case Studies: large or strategic customer logos, pilot programs, testimonials vs. competitors.
- Market Expansion: new regions, offices, verticals, or sales channels being announced.
- Technology & IP: patents, published benchmarks, open-source releases, or claims of technical superiority.
- Reputation & PR: negative press, regulatory actions, awards, analyst reports, or public controversies.
- Events & Public Statements: conference keynotes, product demos, or roadmap announcements that indicate change.
- Financial signals: revenue milestones, IPO/funding news, or explicit market share/trajectory claims.

Context & provenance
--------------------
- Prefer official sources (company accounts, press releases). Treat third-party posts as lower-confidence unless independently corroborated.
- Pay attention to who posts (official account vs employee vs unknown) and where the claim appears (post body vs comments).
- Distinguish explicit facts ("we launched X on 2025-09-01") from speculation / opinion ("might disrupt the market").

Output requirements (STRICT)
---------------------------
Return ONLY a single JSON object with EXACT keys and valid JSON (no extra text, no markdown). Schema:

{
  "is_alert": true|false,               // boolean
  "confidence": 0.0-1.0,               // float: model's confidence
  "reason": "short explanation (1-2 sentences)", 
  "suggested_title": "short title (<=10 words)",
  "suggested_message": "actionable message with why it matters and suggested next step",
  "suggested_severity": "low|medium|high"
}

If uncertain, return is_alert=false with confidence 0.0-0.3 and explain the ambiguity in 'reason'.

Important scoring heuristics
----------------------------
- High (>=0.85): clear, specific, and high-impact signals (e.g., confirmed major customer win, large funding, product launch with proof).
- Medium (0.5-0.85): plausible risk signals that need human review (e.g., pilot with big customer, announcement of hiring plans).
- Low (<0.5): weak or irrelevant signals (team events, sponsorships, non-strategic mentions).

Few-shot examples (RESPOND WITH JSON ONLY)
------------------------------------------
### Example 1 — HIGH alert
Input summary: Official post from CompetitorX: "Launching Acme-Compete AI platform next week; beta access available for enterprise customers."
Expected JSON:
{
  "is_alert": true,
  "confidence": 0.92,
  "reason": "Official product launch announcement for an enterprise AI platform signals direct competitive threat to target company.",
  "suggested_title": "CompetitorX launches enterprise AI platform",
  "suggested_message": "CompetitorX announced a new enterprise AI platform with beta access for enterprise customers. This is a direct product-level threat — monitor feature set and top customers; notify product and sales teams.",
  "suggested_severity": "high"
}

### Example 2 — LOW / No alert
Input summary: Team post: "We sponsored a local hackathon — great turnout!"
Expected JSON:
{
  "is_alert": false,
  "confidence": 0.10,
  "reason": "This is a local sponsorship/community event with no competitive product, hiring, or financial signals.",
  "suggested_title": "No competitor risk detected",
  "suggested_message": "Post describes community engagement and sponsorship; not relevant to competitive dynamics. Action: none needed.",
  "suggested_severity": "low"
}

### Example 3 — MEDIUM alert (ambiguous)
Input summary: Employee post: "We're hiring 30 ML engineers for a 'new initiative' — details soon."
Expected JSON:
{
  "is_alert": true,
  "confidence": 0.65,
  "reason": "Significant hiring in ML indicates possible product/R&D expansion but lacks public detail; warrants monitoring.",
  "suggested_title": "Competitor hiring indicates ML expansion",
  "suggested_message": "Competitor announced hiring 30 ML engineers for an unspecified initiative. This suggests an R&D push that could affect talent supply or product roadmap. Action: monitor for job descriptions and public announcements.",
  "suggested_severity": "medium"
}

Final notes
-----------
- Use metadata.target_company to bias detection (treat posts that mention that company or its customers as higher priority).
- If the post contains verifiable links (press release, blog, PR), mention 'source: link' in the suggested_message to help triage.
- Always return strictly valid JSON — no commentary outside the JSON block.
"""
]


    if metadata:
        meta_lines = [f"{k}: {v}" for k, v in metadata.items()]
        pieces.append("\n\nMetadata:\n" + "\n".join(meta_lines))

    pieces.append("\n\nMain post:\n")
    pieces.append(post_text or "(no text)")

    pieces.append("\n\nComments and replies (most relevant first):\n")

    # flatten comments into concise lines with a hard cap
    comment_count = 0
    for c in comments:
        if comment_count >= 200:
            pieces.append("[...comment list truncated due to length...]")
            break
        author = c.get("author") or c.get("author_profile") or c.get("user") or "anon"
        text = (c.get("text") or c.get("body") or "").strip()
        if not text:
            continue
        pieces.append(f"- {author}: {text}")
        comment_count += 1
        for r in c.get("replies", [])[:2]:
            ra = r.get("author") or r.get("author_profile") or "anon"
            rt = (r.get("text") or r.get("body") or "").strip()
            if rt:
                pieces.append(f"   - reply {ra}: {rt}")
                comment_count += 1
                if comment_count >= 200:
                    break

    pieces.append(
        "\n\nINSTRUCTIONS (IMPORTANT):\n"
        "1) Decide whether this post should raise a COMPETITOR ALERT for the target company.\n"
        "2) Respond ONLY with valid JSON matching this exact schema (no extra text):\n"
        "{\n"
        '  "is_alert": true|false,\n'
        '  "confidence": 0.0-1.0,\n'
        '  "reason": "short explanation (1-2 sentences)",\n'
        '  "suggested_title": "short alert title (10 words or less)",\n'
        '  "suggested_message": "detailed alert message",\n'
        '  "suggested_severity": "low|medium|high"\n'
        "}\n"
        "3) If uncertain, choose is_alert=false with a low confidence (0.0-0.3) and explain why.\n"
        "4) Keep title concise and message actionable (what happened, why it matters, recommended next step).\n"
        "5) Do NOT include any text outside the JSON object."
    )

    prompt = "\n".join(pieces)
    if len(prompt) > max_chars:
        prompt = prompt[: max_chars - 200] + "\n\n[TRUNCATED]"
    return prompt

# ----- Robust JSON extraction helpers -----
def _extract_balanced_json(s: str) -> Optional[str]:
    """
    Find the first balanced JSON object in string s.
    Ignores braces inside quoted strings.
    """
    if not s:
        return None
    start = s.find("{")
    if start == -1:
        return None

    in_str = False
    escape = False
    quote_char = None
    depth = 0
    for i in range(start, len(s)):
        ch = s[i]
        if escape:
            escape = False
            continue
        if ch == "\\":
            escape = True
            continue
        if in_str:
            if ch == quote_char:
                in_str = False
            continue
        else:
            if ch == '"' or ch == "'":
                in_str = True
                quote_char = ch
                continue
            if ch == "{":
                depth += 1
            elif ch == "}":
                depth -= 1
                if depth == 0:
                    return s[start:i+1]
    return None

def _extract_json_from_text(out_text: str) -> Optional[str]:
    """
    Try several strategies to extract and normalize a JSON object returned by an LLM:
      1) Extract a balanced {...} block ignoring braces inside strings.
      2) Try json.loads directly.
      3) Try unicode_escape decoding and json.loads.
      4) Carefully convert single-quoted keys/values -> double quotes and json.loads.
      5) Last-resort: ast.literal_eval() then json.dumps.
    Returns a JSON string (double-quoted) or None on failure.
    """
    if out_text is None:
        return None

    jt = out_text.strip()
    jt = re.sub(r"^```(?:json)?\s*", "", jt, flags=re.I)
    jt = re.sub(r"\s*```$", "", jt, flags=re.I)

    candidate = _extract_balanced_json(jt) or jt

    # 1) direct json
    try:
        json.loads(candidate)
        return candidate
    except Exception:
        pass

    # 2) decode escape sequences (e.g., \" sequences)
    try:
        cand2 = bytes(candidate, "utf-8").decode("unicode_escape")
    except Exception:
        cand2 = candidate

    try:
        json.loads(cand2)
        return cand2
    except Exception:
        pass

    # 3) careful single-quote -> double-quote conversions (heuristic)
    cand3 = cand2
    # convert property names like 'key': -> "key":
    cand3 = re.sub(r"(?P<prefix>(?:\{|,)\s*)'(?P<key>[^']+?)'\s*:", r'\g<prefix>"\g<key>":', cand3)
    # convert single-quoted values : 'value' to "value"
    cand3 = re.sub(r":\s*'(?P<val>[^']*?)'(?P<post>\s*(?:,|\}))", r': "\g<val>"\g<post>', cand3)
    # remove trailing commas
    cand3 = re.sub(r",\s*([}\]])", r"\1", cand3)

    try:
        json.loads(cand3)
        return cand3
    except Exception:
        pass

    # 4) ast.literal_eval fallback (handle Python dict style)
    try:
        pyobj = ast.literal_eval(candidate)
        return json.dumps(pyobj)
    except Exception:
        pass

    return None

# ----- Main analyzer -----
def analyze_post_alert(
    openai_client,
    post_text: str,
    comments: List[Dict[str, Any]],
    metadata: Optional[Dict[str, Any]] = None,
    model: str = "gpt-4o-mini",
    max_tokens: int = 512,
    temperature: float = 0.0,
    timeout: int = 60
) -> Tuple[Dict[str, Any], Optional[str]]:
    """
    Sends post+comments to the LLM and expects JSON matching LLMAlertRawModel.
    Returns (alert_dict, error_code) where alert_dict matches AlertResponseModel if success,
    else a dict describing the failure and an error code string.
    The openai_client must implement: openai_client.chat.completions.create(model=..., messages=..., ...)
    which returns an object where resp.choices[0].message["content"] (or resp.choices[0].text) contains the text.
    """
    prompt = _build_alert_prompt(post_text=post_text, comments=comments, metadata=metadata)

    system_msg = {
        "role": "system",
        "content": (
            "You are a strict JSON-output assistant. Produce ONLY a single JSON object that exactly matches "
            "the instructed schema. Do not add commentary outside the JSON."
        )
    }
    user_msg = {"role": "user", "content": prompt}

    try:
        resp = openai_client.chat.completions.create(
            model=model,
            messages=[system_msg, user_msg],
            max_tokens=max_tokens,
            temperature=temperature,
        )

        # robustly obtain the content text
        out_text = None
        try:
            out_text = resp.choices[0].message["content"]
        except Exception:
            try:
                out_text = resp.choices[0].text
            except Exception:
                out_text = str(resp)

        logger.debug("LLM raw output (truncated 1000 chars): %s", (out_text or "")[:1000])

        raw_json_text = _extract_json_from_text(out_text)
        if not raw_json_text:
            logger.exception("Failed to extract JSON from LLM output. Raw output: %s", (out_text or "")[:1000])
            return (
                {
                    "title": "No alert (parse failure)",
                    "message": "LLM response could not be parsed. Raw output: " + (out_text or "")[:400],
                    "severity": "low",
                },
                "parse_error",
            )

        # parse JSON
        try:
            parsed = json.loads(raw_json_text)
        except Exception:
            try:
                parsed = json.loads(raw_json_text.replace("'", '"'))
            except Exception as e_parse:
                logger.exception("Failed to parse LLM JSON after fallbacks: %s", e_parse)
                return (
                    {
                        "title": "No alert (parse failure)",
                        "message": "LLM response could not be parsed. Raw output: " + (out_text or "")[:400],
                        "severity": "low",
                    },
                    "parse_error",
                )

        # validate / coerce to LLMAlertRawModel
        try:
            llm_raw = LLMAlertRawModel.model_validate(parsed)
        except ValidationError:
            coerced = {
                "is_alert": bool(parsed.get("is_alert") or parsed.get("alert") or parsed.get("should_alert") or False),
                "confidence": float(parsed.get("confidence") or parsed.get("score") or 0.0),
                "reason": str(parsed.get("reason") or parsed.get("explanation") or parsed.get("why") or "")[:1000],
                "suggested_title": parsed.get("suggested_title") or parsed.get("title") or None,
                "suggested_message": parsed.get("suggested_message") or parsed.get("message") or None,
                "suggested_severity": (parsed.get("suggested_severity") or parsed.get("severity") or None),
            }
            try:
                llm_raw = LLMAlertRawModel.model_validate(coerced)
            except ValidationError as e2:
                logger.exception("LLM response failed to validate: %s", e2)
                return (
                    {
                        "title": "No alert (validation failure)",
                        "message": "LLM returned unexpected schema. Raw parsed JSON: " + json.dumps(parsed)[:400],
                        "severity": "low",
                    },
                    "validation_error",
                )

        # map to final severity/title/message
        sev = (llm_raw.suggested_severity or "").lower() if llm_raw.suggested_severity else None
        if sev not in ("low", "medium", "high"):
            if not llm_raw.is_alert:
                sev = "low"
            else:
                if llm_raw.confidence >= 0.85:
                    sev = "high"
                elif llm_raw.confidence >= 0.5:
                    sev = "medium"
                else:
                    sev = "low"

        title = (llm_raw.suggested_title or "").strip()
        if not title:
            reason_snippet = (llm_raw.reason or "").split(".")[0][:80]
            title = ("Competitor alert: " + reason_snippet).strip()

        message = (llm_raw.suggested_message or "").strip()
        if not message:
            message = (
                f"LLM reason: {llm_raw.reason.strip()}\n"
                f"Confidence: {llm_raw.confidence:.2f}\n"
                "Action: Review the post and decide whether to escalate."
            )

        alert_obj = AlertResponseModel(title=title, message=message, severity=sev)
        return (alert_obj.model_dump(), None)

    except Exception as oe:
        logger.exception("OpenAI API call failed: %s", oe)
        return (
            {
                "title": "No alert (API error)",
                "message": f"OpenAI API error: {str(oe)}",
                "severity": "low",
            },
            "openai_error",
        )


# ---------- main integrator ----------

def scrape_posts_with_comments(driver,
                               openai_api_key: Optional[str] = None,
                               post_selector: str = "div.fie-impression-container, div.occludable-update, div[data-urn^='urn:li:activity']",
                               scroll_times: int = 5,
                               scroll_pause: float = 0.5,
                               days: int = 7,
                               max_posts: Optional[int] = None,
                               save_json: str = "linkedin_posts_with_threads_and_sentiment.json",
                               company_base_url: Optional[str] = None,
                               save_pdf_dir: Optional[str] = None,
                               openai_model: str = "gpt-4o-mini"):
    """
    Scans company posts (CSS only), builds correct permalinks and threads, dedup media,
    calls OpenAI once per post (post+comments) to compute sentiment, validates with pydantic.
    """
    cutoff = datetime.now() - timedelta(days=days)
    results = []
    seen = set()
    driver.get(company_base_url)

    if openai_api_key is None:
        openai_api_key = os.environ.get("OPENAI_API_KEY")
    if not openai_api_key:
        raise RuntimeError("OpenAI API key not found. Set OPENAI_API_KEY or pass openai_api_key.")

    openai_client = OpenAI(api_key=openai_api_key)

    # pre-scroll
    for _ in range(scroll_times):
        try:
            driver.execute_script("window.scrollBy(0, Math.max(document.documentElement.clientHeight, 800));")
            time.sleep(scroll_pause)
        except Exception:
            break

    try:
        post_elems = driver.find_elements(By.CSS_SELECTOR, post_selector)
    except Exception:
        post_elems = []

    for el in post_elems:
        if max_posts and len(results) >= max_posts:
            break
        try:
            uid = (el.get_attribute("data-urn") or el.get_attribute("id") or el.get_attribute("data-entity-urn") or "") or (_safe_text(el)[:200])
            if not uid:
                uid = f"post_{len(results)}"
            if uid in seen:
                continue
            seen.add(uid)

            permalink = _get_post_permalink(el, driver, company_base_url=company_base_url)
            # guarantee permalink not null: fallback
            if not permalink:
                # try anchor in header
                href = _find_anchor_href_in_el(el)
                if href:
                    permalink = href if href.startswith("http") else "https://www.linkedin.com" + href
            if not permalink:
                # fallback synthetic
                permalink = f"{company_base_url or 'https://www.linkedin.com'}/posts/{uid}"

            # text
            text = ""
            try:
                try:
                    txt_el = el.find_element(By.CSS_SELECTOR, "div.update-components-text, div.update-components-update-v2__commentary, span.break-words, div.feed-shared-text")
                    text = driver.execute_script("return arguments[0].textContent", txt_el) or txt_el.text or ""
                except Exception:
                    text = _safe_text(el)
                text = (text or "").strip()
            except Exception:
                text = ""

            # time
            raw_time = ""
            try:
                time_el = el.find_element(By.CSS_SELECTOR, "time")
                raw_time = time_el.get_attribute("datetime") or time_el.text or ""
            except Exception:
                try:
                    raw_time = _safe_text(el.find_element(By.CSS_SELECTOR, ".update-components-actor__sub-description"))
                except Exception:
                    raw_time = ""

            # images
            images = []
            try:
                imgs = el.find_elements(By.CSS_SELECTOR, "div.update-components-image img, img.update-components-image__image, img.ivm-view-attr__img--centered, img.feed-shared-image__image")
                for im in imgs:
                    try:
                        v = im.get_attribute("src") or im.get_attribute("data-src") or im.get_attribute("data-delayed-url") or ""
                        if v and not v.startswith("data:"):
                            images.append(v.split("?")[0] if "?" in v else v)
                    except Exception:
                        continue
            except Exception:
                images = []

            # videos
            videos = []
            try:
                vids = el.find_elements(By.CSS_SELECTOR, "video, iframe, div.video-entity, a[href*='.mp4']")
                for v in vids:
                    try:
                        vs = v.get_attribute("src") or v.get_attribute("data-src") or v.get_attribute("href") or ""
                        if vs:
                            videos.append(vs.split("?")[0] if "?" in vs else vs)
                    except Exception:
                        continue
            except Exception:
                videos = []

            # attachments -> PDFs and other anchors
            pdfs = []
            try:
                anchors = el.find_elements(By.CSS_SELECTOR, "a[href]")
                for a in anchors:
                    try:
                        href = a.get_attribute("href") or ""
                        if href.lower().endswith(".pdf"):
                            pdfs.append(href)
                    except Exception:
                        continue
            except Exception:
                pdfs = []

            # dedupe images/videos but preserve order
            images = _unique_preserve_order(images)
            videos = _unique_preserve_order(videos)

            # save pdfs if requested
            saved_pdfs = []
            if save_pdf_dir and pdfs:
                os.makedirs(save_pdf_dir, exist_ok=True)
                for p in _unique_preserve_order(pdfs):
                    try:
                        # attempt to download file (requests not imported by default)
                        # we implement a minimal download using urllib to avoid adding extra deps
                        from urllib.request import urlopen, Request
                        req = Request(p, headers={"User-Agent": "Mozilla/5.0"})
                        with urlopen(req, timeout=20) as resp:
                            data = resp.read()
                            filename = os.path.join(save_pdf_dir, os.path.basename(p.split("?")[0]))
                            with open(filename, "wb") as fh:
                                fh.write(data)
                            saved_pdfs.append(filename)
                    except Exception:
                        # ignore download errors, but keep link in metadata
                        saved_pdfs.append(p)

            # social counts
            social_counts = {"reactions_count": None, "comments_count": None, "reposts_count": None, "reaction_types": []}
            try:
                soc = el.find_element(By.CSS_SELECTOR, "div.social-details-social-counts, div.update-v2-social-activity, .social-details-social-counts")
                try:
                    # reactions count
                    btn = soc.find_element(By.CSS_SELECTOR, "button[data-reaction-details], button[aria-label*='reactions'], li.social-details-social-counts__reactions button")
                    rc_txt = (btn.text or btn.get_attribute("textContent") or "").strip()
                    m = re.search(r'([\d,]+)', rc_txt)
                    if m:
                        social_counts["reactions_count"] = int(m.group(1).replace(",", ""))
                except Exception:
                    pass
                try:
                    # comments_count
                    cbtn = soc.find_element(By.CSS_SELECTOR, "li.social-details-social-counts__comments button, button[aria-label*='comments']")
                    c_txt = (cbtn.text or cbtn.get_attribute("textContent") or "").strip()
                    m = re.search(r'([\d,]+)', c_txt)
                    if m:
                        social_counts["comments_count"] = int(m.group(1).replace(",", ""))
                except Exception:
                    pass
                try:
                    rbtn = soc.find_element(By.CSS_SELECTOR, "li.social-details-social-counts__item button[aria-label*='repost'], li.social-details-social-counts__item button[aria-label*='reposts'], button[aria-label*='repost']")
                    r_txt = (rbtn.text or rbtn.get_attribute("textContent") or "").strip()
                    m = re.search(r'([\d,]+)', r_txt)
                    if m:
                        social_counts["reposts_count"] = int(m.group(1).replace(",", ""))
                except Exception:
                    pass
                # reaction types from imgs
                try:
                    imgs = soc.find_elements(By.CSS_SELECTOR, "img[data-test-reactions-icon-type]")
                    types = []
                    for i in imgs:
                        try:
                            t = i.get_attribute("data-test-reactions-icon-type")
                            if t:
                                types.append(t)
                        except Exception:
                            continue
                    social_counts["reaction_types"] = _unique_preserve_order(types)
                except Exception:
                    pass
            except Exception:
                pass

            # collect full comment threads
            comments_thread = []
            try:
                comments_thread = _collect_all_comments_for_post(el, driver,
                                                                max_expand_clicks=12,
                                                                reply_expand_clicks=25,
                                                                per_post_timeout=20)
            except Exception:
                comments_thread = []

            # build post object BEFORE sentiment so we can attach comment ids etc.
            post_obj = {
                "uid": uid,
                "permalink": permalink,
                "post_url": permalink,
                "text": text,
                "raw_time": raw_time,
                "images": images,
                "videos": videos,
                "pdfs": pdfs,
                "saved_pdfs": saved_pdfs,
                "social_counts": social_counts,
                "comments_thread": comments_thread,
                "post_sentiment": None,
                "comments_sentiment_summary": None
            }

            # Prepare single API call per post: pass post text + all comments flattened
            # Build comments payload for LLM: flatten comments to a simpler list
            flattened_comments = []

            def _flatten_comments_for_llm(ct):
                out = []
                for c in ct:
                    item = {
                        "author": c.get("author"),
                        "author_profile": c.get("author_profile"),
                        "text": c.get("text"),
                        "raw_time": c.get("raw_time"),
                        "reactions": c.get("reactions")
                    }
                    out.append(item)
                    if c.get("replies"):
                        # include few replies to keep context
                        for r in c.get("replies", [])[:3]:
                            out.append({
                                "author": r.get("author"),
                                "author_profile": r.get("author_profile"),
                                "text": r.get("text"),
                                "raw_time": r.get("raw_time"),
                                "reactions": r.get("reactions"),
                                "is_reply": True
                            })
                return out

            flattened_comments = _flatten_comments_for_llm(comments_thread)

            # run sentiment analysis single call
            try:
                sentiment_result, err = analyze_post_sentiment(openai_client, text, flattened_comments, model=openai_model)
                aleart_result,err = analyze_post_alert(openai_client, text, flattened_comments, model=openai_model)
                post_obj["post_alert"] = aleart_result
                post_obj["post_sentiment"] = sentiment_result
            except Exception as e:
                post_obj["post_sentiment"] = {"label":"neutral","score":0.0,"explanation":f"error:{str(e)}"}

            # compute comments summary by calling LLM? (we already ran single call per post for overall)
            # The requirement: "for single post there will be a single api call." So we'll compute comments summary locally from individual comment sentiment placeholders
            # To keep one API call per post, we will not call LLM per comment. We set per-comment sentiment as None (or we could reuse LLM output if it included per-comment labels, but we asked overall).
            # We'll compute a neutral summary placeholder plus any available numeric reaction/comment counts.
            try:
                total_comments = social_counts.get("comments_count") or len([c for c in comments_thread if c])
                post_obj["comments_sentiment_summary"] = {
                    "total_comments": total_comments,
                    "positive": 0,
                    "neutral": total_comments,
                    "negative": 0,
                    "average_score": post_obj["post_sentiment"].get("score", 0.0),
                    "error": err or ""
                }
            except Exception:
                post_obj["comments_sentiment_summary"] = {
                    "total_comments": len(comments_thread),
                    "positive": 0,
                    "neutral": len(comments_thread),
                    "negative": 0,
                    "average_score": post_obj["post_sentiment"].get("score", 0.0),
                    "error": "summary_error"
                }

            results.append(post_obj)

        except StaleElementReferenceException:
            continue
        except Exception:
            continue

    # # save
    # try:
    #     with open(save_json, "w", encoding="utf-8") as fh:
    #         json.dump(results, fh, ensure_ascii=False, indent=2)
    #     print(f"Saved {len(results)} posts to {save_json}")
    # except Exception as e:
    #     print("Failed to save JSON:", e)
    # print(f"Scraped {len(results)} posts from page.",results)
    processed_data=process_linkedin_data(results)
    # try:
    #     with open("processed_data_from_crawler.json", "w", encoding="utf-8") as fh:
    #         json.dump(processed_data, fh, ensure_ascii=False, indent=2)
    #     print(f"Saved {len(processed_data)} posts to processed_data_from_crawler.json")
    # except Exception as e:
    #     print("Failed to save JSON:", e)

    return processed_data





In [59]:
print(scrape_posts_with_comments(drivers, openai_api_key=openai_key, company_base_url="https://www.linkedin.com/school/udacity/posts", save_pdf_dir="./pdfs")  )

DEBUG:selenium.webdriver.remote.remote_connection:POST http://localhost:58740/session/9d5352700a64aa3396bab246012c5a4f/url {'url': 'https://www.linkedin.com/school/udacity/posts'}
DEBUG:urllib3.connectionpool:http://localhost:58740 "POST /session/9d5352700a64aa3396bab246012c5a4f/url HTTP/1.1" 200 0
DEBUG:selenium.webdriver.remote.remote_connection:Remote response: status=200 | data={"value":null} | headers=HTTPHeaderDict({'Content-Length': '14', 'Content-Type': 'application/json; charset=utf-8', 'cache-control': 'no-cache'})
DEBUG:selenium.webdriver.remote.remote_connection:Finished Request
DEBUG:selenium.webdriver.remote.remote_connection:POST http://localhost:58740/session/9d5352700a64aa3396bab246012c5a4f/execute/sync {'script': 'window.scrollBy(0, Math.max(document.documentElement.clientHeight, 800));', 'args': []}
DEBUG:urllib3.connectionpool:http://localhost:58740 "POST /session/9d5352700a64aa3396bab246012c5a4f/execute/sync HTTP/1.1" 200 0
DEBUG:selenium.webdriver.remote.remote_co

Processing 31 posts... [{'uid': 'ember65', 'permalink': 'https://www.linkedin.com/school/udacity/posts/posts/ember65', 'post_url': 'https://www.linkedin.com/school/udacity/posts/posts/ember65', 'text': 'It’s official, Udacity is now a part of Accenture! Since 2011, we’ve transformed innumerable lives, businesses, and nations by delivering cutting-edge skill development in AI, Data, Programming, and beyond. We’ve cheered on our students as they landed their first tech jobs or got that long-awaited promotion, and we’ve celebrated the success of customers who have unlocked exceptional business outcomes.Now, as a part of Accenture, Udacity will be able to support even more professionals across the world and contribute to more life-changing stories. Our mission is to forge futures in tech, and that future just got even brighter ☀️.Read more. 👇https://bit.ly/3UGtEeU', 'raw_time': '1yr • \n 1 year ago • Visible to anyone on or off LinkedIn', 'images': ['https://media.licdn.com/dms/image/v2/C5

In [60]:
posts

[]

In [29]:
# process_linkedin_data_with_alerts.py
import json
from datetime import datetime, timezone
from typing import Any, Dict, List, Optional
import re

OUTPUT_FILENAME = "processed_linkedin_posts.json"

def _parse_posted_at(raw_time: Optional[str]) -> str:
    """
    Try several heuristics to parse a 'raw_time' field from LinkedIn.
    If parsing fails or raw_time is None/empty, return current UTC ISO timestamp.
    """
    if not raw_time:
        return datetime.now(timezone.utc).isoformat()

    # common patterns: "1d • \n 1 day ago • Visible..." or "7h" or "1 day ago"
    s = raw_time.strip()
    # look for patterns like 'YYYY-MM-DD' or ISO (unlikely), else numeric + 'd'/'h'/'m'
    iso_match = re.search(r"\d{4}-\d{2}-\d{2}", s)
    if iso_match:
        try:
            return datetime.fromisoformat(iso_match.group(0)).replace(tzinfo=timezone.utc).isoformat()
        except Exception:
            pass

    # relative times like "7h", "1d", "1 day ago", "1 hour ago"
    rel_match = re.search(r"(\d+)\s*(d|day|days|h|hour|hours|m|minute|minutes)\b", s, flags=re.I)
    if rel_match:
        qty = int(rel_match.group(1))
        unit = rel_match.group(2).lower()
        now = datetime.now(timezone.utc)
        if unit.startswith("d"):
            dt = now - timedelta(days=qty)
        elif unit.startswith("h"):
            dt = now - timedelta(hours=qty)
        elif unit.startswith("m"):
            dt = now - timedelta(minutes=qty)
        else:
            dt = now
        return dt.isoformat()

    # fallback: return current time
    return datetime.now(timezone.utc).isoformat()

def process_linkedin_data(data) -> None:
    """
    Reads the input JSON (expected to include fields like 'post_sentiment' and 'post_alert')
    and writes a processed file that combines:
      - basic post metadata,
      - sentiment (label/score/explanation),
      - comments summary,
      - alert details (title/message/severity and optional confidence)

    Output schema (per post):
    {
      "uid", "company_id", "post_platform", "post_url", "post_description", "posted_at",
      "likes", "comments_count", "shares",
      "sentiment_label", "sentiment_score", "sentiment_explanation",
      "comments_summary": {...},
      "alert": {
         "title", "message", "severity", "confidence" (optional)
      }
    }
    """

    processed_posts: List[Dict[str, Any]] = []
    company_id_counter = 1  # simple company id for all posts (adjust as needed)

    for post in data:
        # only process items that look like LinkedIn posts (original code checked uid prefix)
        uid = post.get('uid') or ""
        if not isinstance(uid, str) or not uid.startswith('urn:li:activity:'):
            # optionally still process non-standard entries — here we skip to match previous behavior
            continue

        social_counts = post.get('social_counts') or {}
        post_sentiment = post.get('post_sentiment') or {}
        comments_summary = post.get('comments_sentiment_summary') or {}

        # extract alert info if present
        post_alert = post.get('post_alert') or {}
        alert_title = post_alert.get('title')
        alert_message = post_alert.get('message')
        alert_severity = post_alert.get('severity')
        # some LLM outputs may include confidence or score; try common names
        alert_confidence = post_alert.get('confidence') or post_alert.get('score') or post_alert.get('confidence_score')

        # build processed object
        processed_post: Dict[str, Any] = {
            "uid": uid,
            "company_id": company_id_counter,
            "post_platform": "linkedin",
            "post_url": post.get('post_url'),
            "post_description": post.get('text'),
            # try to parse posted time; fall back to now
            "posted_at": _parse_posted_at(post.get('raw_time') or post.get('raw_time_text') or ""),
            "likes": social_counts.get('reactions_count') if social_counts.get('reactions_count') is not None else 0,
            "comments_count": social_counts.get('comments_count') if social_counts.get('comments_count') is not None else 0,
            "shares": social_counts.get('reposts_count') if social_counts.get('reposts_count') is not None else 0,
            # sentiment
            "sentiment_label": post_sentiment.get('label'),
            "sentiment_score": post_sentiment.get('score'),
            "sentiment_explanation": post_sentiment.get('explanation'),
            # comments summary (keep raw structure to allow further processing)
            "comments_summary": {
                "total_comments": comments_summary.get('total_comments'),
                "positive": comments_summary.get('positive'),
                "neutral": comments_summary.get('neutral'),
                "negative": comments_summary.get('negative'),
                "average_score": comments_summary.get('average_score'),
                "error": comments_summary.get('error', "")
            },
            # alert block
            "alert": {
                "title": alert_title or None,
                "message": alert_message or None,
                "severity": alert_severity or None,
                "confidence": float(alert_confidence) if alert_confidence is not None else None
            }
        }

        processed_posts.append(processed_post)

    # write out
    with open(output_filename, 'w', encoding='utf-8') as f:
        json.dump(processed_posts, f, indent=4, ensure_ascii=False)

    print(f"Processing complete. The new file has been saved as '{output_filename}'")
    print(f"Total posts processed: {len(processed_posts)}")





In [ ]:
# alert_analyzer.py
import re
import json
import ast
import logging
from typing import List, Dict, Any, Tuple, Optional
from pydantic import BaseModel, Field, ValidationError

logger = logging.getLogger(__name__)
logging.basicConfig(level=logging.DEBUG)  # change to INFO in production

# ----- Models -----
class AlertResponseModel(BaseModel):
    title: str = Field(..., description="Title of the alert in 10 words or less")
    message: str = Field(..., description="Detailed message of the alert")
    severity: str = Field(..., description="Severity level of the alert (low|medium|high)")

class LLMAlertRawModel(BaseModel):
    """
    Expected raw LLM response shape. We ask the LLM to return exactly this JSON.
    """
    is_alert: bool
    confidence: float
    reason: str
    suggested_title: Optional[str] = None
    suggested_message: Optional[str] = None
    suggested_severity: Optional[str] = None

# ----- Prompt builder -----
def _build_alert_prompt(
    post_text: str,
    comments: List[Dict[str, Any]],
    metadata: Optional[Dict[str, Any]] = None,
    max_chars: int = 12000
) -> str:
    """
    Compose the prompt that will be sent to the LLM.
    Uses a detailed competitor-intelligence instruction set.
    """
    pieces = [
    """You are a COMPETITOR INTELLIGENCE classification assistant.

Your job
------
Decide whether a LinkedIn post (including its comments/replies) should trigger a COMPETITOR ALERT for the *target company* (use metadata.target_company when available). A COMPETITOR ALERT means the post contains timely, verifiable, or plausible information that may affect the target company's strategy, product competitiveness, hiring, market share, or reputation.

What to look for (signals)
--------------------------
- Product & Service Launches: new products, betas, feature rollouts, rebrands, or explicit product claims.
- Pricing & Promotions: pricing model changes, large discounts, free tiers, or claims like "40% cheaper".
- Hiring & Talent Moves: large hires, new R&D centers, key exec moves, or targeted recruitment campaigns.
- Partnerships, M&A & Funding: alliances, integrations, acquisitions, funding rounds, or investor news.
- Customer Wins & Case Studies: large or strategic customer logos, pilot programs, testimonials vs. competitors.
- Market Expansion: new regions, offices, verticals, or sales channels being announced.
- Technology & IP: patents, published benchmarks, open-source releases, or claims of technical superiority.
- Reputation & PR: negative press, regulatory actions, awards, analyst reports, or public controversies.
- Events & Public Statements: conference keynotes, product demos, or roadmap announcements that indicate change.
- Financial signals: revenue milestones, IPO/funding news, or explicit market share/trajectory claims.

Context & provenance
--------------------
- Prefer official sources (company accounts, press releases). Treat third-party posts as lower-confidence unless independently corroborated.
- Pay attention to who posts (official account vs employee vs unknown) and where the claim appears (post body vs comments).
- Distinguish explicit facts ("we launched X on 2025-09-01") from speculation / opinion ("might disrupt the market").

Output requirements (STRICT)
---------------------------
Return ONLY a single JSON object with EXACT keys and valid JSON (no extra text, no markdown). Schema:

{
  "is_alert": true|false,               // boolean
  "confidence": 0.0-1.0,               // float: model's confidence
  "reason": "short explanation (1-2 sentences)", 
  "suggested_title": "short title (<=10 words)",
  "suggested_message": "actionable message with why it matters and suggested next step",
  "suggested_severity": "low|medium|high"
}

If uncertain, return is_alert=false with confidence 0.0-0.3 and explain the ambiguity in 'reason'.

Important scoring heuristics
----------------------------
- High (>=0.85): clear, specific, and high-impact signals (e.g., confirmed major customer win, large funding, product launch with proof).
- Medium (0.5-0.85): plausible risk signals that need human review (e.g., pilot with big customer, announcement of hiring plans).
- Low (<0.5): weak or irrelevant signals (team events, sponsorships, non-strategic mentions).

Few-shot examples (RESPOND WITH JSON ONLY)
------------------------------------------
### Example 1 — HIGH alert
Input summary: Official post from CompetitorX: "Launching Acme-Compete AI platform next week; beta access available for enterprise customers."
Expected JSON:
{
  "is_alert": true,
  "confidence": 0.92,
  "reason": "Official product launch announcement for an enterprise AI platform signals direct competitive threat to target company.",
  "suggested_title": "CompetitorX launches enterprise AI platform",
  "suggested_message": "CompetitorX announced a new enterprise AI platform with beta access for enterprise customers. This is a direct product-level threat — monitor feature set and top customers; notify product and sales teams.",
  "suggested_severity": "high"
}

### Example 2 — LOW / No alert
Input summary: Team post: "We sponsored a local hackathon — great turnout!"
Expected JSON:
{
  "is_alert": false,
  "confidence": 0.10,
  "reason": "This is a local sponsorship/community event with no competitive product, hiring, or financial signals.",
  "suggested_title": "No competitor risk detected",
  "suggested_message": "Post describes community engagement and sponsorship; not relevant to competitive dynamics. Action: none needed.",
  "suggested_severity": "low"
}

### Example 3 — MEDIUM alert (ambiguous)
Input summary: Employee post: "We're hiring 30 ML engineers for a 'new initiative' — details soon."
Expected JSON:
{
  "is_alert": true,
  "confidence": 0.65,
  "reason": "Significant hiring in ML indicates possible product/R&D expansion but lacks public detail; warrants monitoring.",
  "suggested_title": "Competitor hiring indicates ML expansion",
  "suggested_message": "Competitor announced hiring 30 ML engineers for an unspecified initiative. This suggests an R&D push that could affect talent supply or product roadmap. Action: monitor for job descriptions and public announcements.",
  "suggested_severity": "medium"
}

Final notes
-----------
- Use metadata.target_company to bias detection (treat posts that mention that company or its customers as higher priority).
- If the post contains verifiable links (press release, blog, PR), mention 'source: link' in the suggested_message to help triage.
- Always return strictly valid JSON — no commentary outside the JSON block.
"""
]


    if metadata:
        meta_lines = [f"{k}: {v}" for k, v in metadata.items()]
        pieces.append("\n\nMetadata:\n" + "\n".join(meta_lines))

    pieces.append("\n\nMain post:\n")
    pieces.append(post_text or "(no text)")

    pieces.append("\n\nComments and replies (most relevant first):\n")

    # flatten comments into concise lines with a hard cap
    comment_count = 0
    for c in comments:
        if comment_count >= 200:
            pieces.append("[...comment list truncated due to length...]")
            break
        author = c.get("author") or c.get("author_profile") or c.get("user") or "anon"
        text = (c.get("text") or c.get("body") or "").strip()
        if not text:
            continue
        pieces.append(f"- {author}: {text}")
        comment_count += 1
        for r in c.get("replies", [])[:2]:
            ra = r.get("author") or r.get("author_profile") or "anon"
            rt = (r.get("text") or r.get("body") or "").strip()
            if rt:
                pieces.append(f"   - reply {ra}: {rt}")
                comment_count += 1
                if comment_count >= 200:
                    break

    pieces.append(
        "\n\nINSTRUCTIONS (IMPORTANT):\n"
        "1) Decide whether this post should raise a COMPETITOR ALERT for the target company.\n"
        "2) Respond ONLY with valid JSON matching this exact schema (no extra text):\n"
        "{\n"
        '  "is_alert": true|false,\n'
        '  "confidence": 0.0-1.0,\n'
        '  "reason": "short explanation (1-2 sentences)",\n'
        '  "suggested_title": "short alert title (10 words or less)",\n'
        '  "suggested_message": "detailed alert message",\n'
        '  "suggested_severity": "low|medium|high"\n'
        "}\n"
        "3) If uncertain, choose is_alert=false with a low confidence (0.0-0.3) and explain why.\n"
        "4) Keep title concise and message actionable (what happened, why it matters, recommended next step).\n"
        "5) Do NOT include any text outside the JSON object."
    )

    prompt = "\n".join(pieces)
    if len(prompt) > max_chars:
        prompt = prompt[: max_chars - 200] + "\n\n[TRUNCATED]"
    return prompt

# ----- Robust JSON extraction helpers -----
def _extract_balanced_json(s: str) -> Optional[str]:
    """
    Find the first balanced JSON object in string s.
    Ignores braces inside quoted strings.
    """
    if not s:
        return None
    start = s.find("{")
    if start == -1:
        return None

    in_str = False
    escape = False
    quote_char = None
    depth = 0
    for i in range(start, len(s)):
        ch = s[i]
        if escape:
            escape = False
            continue
        if ch == "\\":
            escape = True
            continue
        if in_str:
            if ch == quote_char:
                in_str = False
            continue
        else:
            if ch == '"' or ch == "'":
                in_str = True
                quote_char = ch
                continue
            if ch == "{":
                depth += 1
            elif ch == "}":
                depth -= 1
                if depth == 0:
                    return s[start:i+1]
    return None

def _extract_json_from_text(out_text: str) -> Optional[str]:
    """
    Try several strategies to extract and normalize a JSON object returned by an LLM:
      1) Extract a balanced {...} block ignoring braces inside strings.
      2) Try json.loads directly.
      3) Try unicode_escape decoding and json.loads.
      4) Carefully convert single-quoted keys/values -> double quotes and json.loads.
      5) Last-resort: ast.literal_eval() then json.dumps.
    Returns a JSON string (double-quoted) or None on failure.
    """
    if out_text is None:
        return None

    jt = out_text.strip()
    jt = re.sub(r"^```(?:json)?\s*", "", jt, flags=re.I)
    jt = re.sub(r"\s*```$", "", jt, flags=re.I)

    candidate = _extract_balanced_json(jt) or jt

    # 1) direct json
    try:
        json.loads(candidate)
        return candidate
    except Exception:
        pass

    # 2) decode escape sequences (e.g., \" sequences)
    try:
        cand2 = bytes(candidate, "utf-8").decode("unicode_escape")
    except Exception:
        cand2 = candidate

    try:
        json.loads(cand2)
        return cand2
    except Exception:
        pass

    # 3) careful single-quote -> double-quote conversions (heuristic)
    cand3 = cand2
    # convert property names like 'key': -> "key":
    cand3 = re.sub(r"(?P<prefix>(?:\{|,)\s*)'(?P<key>[^']+?)'\s*:", r'\g<prefix>"\g<key>":', cand3)
    # convert single-quoted values : 'value' to "value"
    cand3 = re.sub(r":\s*'(?P<val>[^']*?)'(?P<post>\s*(?:,|\}))", r': "\g<val>"\g<post>', cand3)
    # remove trailing commas
    cand3 = re.sub(r",\s*([}\]])", r"\1", cand3)

    try:
        json.loads(cand3)
        return cand3
    except Exception:
        pass

    # 4) ast.literal_eval fallback (handle Python dict style)
    try:
        pyobj = ast.literal_eval(candidate)
        return json.dumps(pyobj)
    except Exception:
        pass

    return None

# ----- Main analyzer -----
def analyze_post_alert(
    openai_client,
    post_text: str,
    comments: List[Dict[str, Any]],
    metadata: Optional[Dict[str, Any]] = None,
    model: str = "gpt-4o-mini",
    max_tokens: int = 512,
    temperature: float = 0.0,
    timeout: int = 60
) -> Tuple[Dict[str, Any], Optional[str]]:
    """
    Sends post+comments to the LLM and expects JSON matching LLMAlertRawModel.
    Returns (alert_dict, error_code) where alert_dict matches AlertResponseModel if success,
    else a dict describing the failure and an error code string.
    The openai_client must implement: openai_client.chat.completions.create(model=..., messages=..., ...)
    which returns an object where resp.choices[0].message["content"] (or resp.choices[0].text) contains the text.
    """
    prompt = _build_alert_prompt(post_text=post_text, comments=comments, metadata=metadata)

    system_msg = {
        "role": "system",
        "content": (
            "You are a strict JSON-output assistant. Produce ONLY a single JSON object that exactly matches "
            "the instructed schema. Do not add commentary outside the JSON."
        )
    }
    user_msg = {"role": "user", "content": prompt}

    try:
        resp = openai_client.chat.completions.create(
            model=model,
            messages=[system_msg, user_msg],
            max_tokens=max_tokens,
            temperature=temperature,
        )

        # robustly obtain the content text
        out_text = None
        try:
            out_text = resp.choices[0].message["content"]
        except Exception:
            try:
                out_text = resp.choices[0].text
            except Exception:
                out_text = str(resp)

        logger.debug("LLM raw output (truncated 1000 chars): %s", (out_text or "")[:1000])

        raw_json_text = _extract_json_from_text(out_text)
        if not raw_json_text:
            logger.exception("Failed to extract JSON from LLM output. Raw output: %s", (out_text or "")[:1000])
            return (
                {
                    "title": "No alert (parse failure)",
                    "message": "LLM response could not be parsed. Raw output: " + (out_text or "")[:400],
                    "severity": "low",
                },
                "parse_error",
            )

        # parse JSON
        try:
            parsed = json.loads(raw_json_text)
        except Exception:
            try:
                parsed = json.loads(raw_json_text.replace("'", '"'))
            except Exception as e_parse:
                logger.exception("Failed to parse LLM JSON after fallbacks: %s", e_parse)
                return (
                    {
                        "title": "No alert (parse failure)",
                        "message": "LLM response could not be parsed. Raw output: " + (out_text or "")[:400],
                        "severity": "low",
                    },
                    "parse_error",
                )

        # validate / coerce to LLMAlertRawModel
        try:
            llm_raw = LLMAlertRawModel.model_validate(parsed)
        except ValidationError:
            coerced = {
                "is_alert": bool(parsed.get("is_alert") or parsed.get("alert") or parsed.get("should_alert") or False),
                "confidence": float(parsed.get("confidence") or parsed.get("score") or 0.0),
                "reason": str(parsed.get("reason") or parsed.get("explanation") or parsed.get("why") or "")[:1000],
                "suggested_title": parsed.get("suggested_title") or parsed.get("title") or None,
                "suggested_message": parsed.get("suggested_message") or parsed.get("message") or None,
                "suggested_severity": (parsed.get("suggested_severity") or parsed.get("severity") or None),
            }
            try:
                llm_raw = LLMAlertRawModel.model_validate(coerced)
            except ValidationError as e2:
                logger.exception("LLM response failed to validate: %s", e2)
                return (
                    {
                        "title": "No alert (validation failure)",
                        "message": "LLM returned unexpected schema. Raw parsed JSON: " + json.dumps(parsed)[:400],
                        "severity": "low",
                    },
                    "validation_error",
                )

        # map to final severity/title/message
        sev = (llm_raw.suggested_severity or "").lower() if llm_raw.suggested_severity else None
        if sev not in ("low", "medium", "high"):
            if not llm_raw.is_alert:
                sev = "low"
            else:
                if llm_raw.confidence >= 0.85:
                    sev = "high"
                elif llm_raw.confidence >= 0.5:
                    sev = "medium"
                else:
                    sev = "low"

        title = (llm_raw.suggested_title or "").strip()
        if not title:
            reason_snippet = (llm_raw.reason or "").split(".")[0][:80]
            title = ("Competitor alert: " + reason_snippet).strip()

        message = (llm_raw.suggested_message or "").strip()
        if not message:
            message = (
                f"LLM reason: {llm_raw.reason.strip()}\n"
                f"Confidence: {llm_raw.confidence:.2f}\n"
                "Action: Review the post and decide whether to escalate."
            )

        alert_obj = AlertResponseModel(title=title, message=message, severity=sev)
        return (alert_obj.model_dump(), None)

    except Exception as oe:
        logger.exception("OpenAI API call failed: %s", oe)
        return (
            {
                "title": "No alert (API error)",
                "message": f"OpenAI API error: {str(oe)}",
                "severity": "low",
            },
            "openai_error",
        )



DEBUG:httpcore.connection:close.started
DEBUG:httpcore.connection:close.complete
DEBUG:__main__:LLM raw output (truncated 1000 chars): Some wrapper text
```json
{
  'is_alert': True,
  'confidence': 0.72,
  'reason': "CompetitorX announced a pilot with a large client, which may affect our contract renewals.",
  'suggested_title': 'CompetitorX pilots with big client',
  'suggested_message': 'CompetitorX started a pilot with BigCorp; monitor account health and reach out to the customer.',
  'suggested_severity': 'medium'
}
```
-- end


Demo Alert: {
  "title": "CompetitorX pilots with big client",
  "message": "CompetitorX started a pilot with BigCorp; monitor account health and reach out to the customer.",
  "severity": "medium"
}
Error code: None


In [17]:
import os
from openai import OpenAI


# Ensure OPENAI_API_KEY is set in env
client = OpenAI(api_key=os.environ["OPENAI_API_KEY"])

# High-alert example: official launch + named customer + explicit claim + funding
post_text = """
Official: CompetitorX today announced the launch of their enterprise AI hiring platform "HireAI Pro".
They claim HireAI Pro reduces recruitment costs by 40% vs traditional ATS solutions and includes integrations with major HRIS vendors.
CompetitorX also confirmed a $200M Series C to scale enterprise sales and named BigCorp as an early enterprise customer.
"""

comments = [
    {
        "author": "CompetitorX (official)",
        "text": "We're excited to bring HireAI Pro to enterprise customers — early access available for select partners."
    },
    {
        "author": "MarketAnalyst",
        "text": "BigCorp as an early customer and $200M funding is a major signal — this will accelerate their go-to-market."
    },
    {
        "author": "Recruiter101",
        "text": "If true, 40% cost reduction will be disruptive for many ATS vendors."
    }
]

metadata = {
    "company": "Acme Corp",
    "target_company": "Acme Corp",   # used by prompt to bias detection
    "sector": "HR Tech / AI SaaS",
    "source": "LinkedIn - official company post"
}

alert, error = analyze_post_alert(
    openai_client=client,
    post_text=post_text,
    comments=comments,
    metadata=metadata,
    model="gpt-4o-mini",
    max_tokens=512,
    temperature=0.0
)

print("---- Alert Output ----")
print(alert)
print("Error code:", error)


DEBUG:openai._base_client:Request options: {'method': 'post', 'url': '/chat/completions', 'files': None, 'idempotency_key': 'stainless-python-retry-64524b96-f0c2-4113-b87d-72ed606f8c83', 'json_data': {'messages': [{'role': 'system', 'content': 'You are a strict JSON-output assistant. Produce ONLY a single JSON object that exactly matches the instructed schema. Do not add commentary outside the JSON.'}, {'role': 'user', 'content': 'You are a COMPETITOR INTELLIGENCE classification assistant.\n\nYour job\n------\nDecide whether a LinkedIn post (including its comments/replies) should trigger a COMPETITOR ALERT for the *target company* (use metadata.target_company when available). A COMPETITOR ALERT means the post contains timely, verifiable, or plausible information that may affect the target company\'s strategy, product competitiveness, hiring, market share, or reputation.\n\nWhat to look for (signals)\n--------------------------\n- Product & Service Launches: new products, betas, feature

---- Alert Output ----
{'title': 'CompetitorX launches HireAI Pro platform', 'message': "CompetitorX has launched their enterprise AI hiring platform, HireAI Pro, which claims to reduce recruitment costs by 40% compared to traditional ATS solutions. This could significantly impact Acme Corp's market position. Action: analyze the feature set and pricing strategy of HireAI Pro to adjust competitive positioning.", 'severity': 'high'}
Error code: None


In [ ]:
"""
linkedin_playwright_crawler_openai.py

- Playwright (async) crawler for LinkedIn company posts (Recent).
- Downloads images & PDFs attached to a post, collects comments, reactions, shares.
- Integrates with OpenAI Responses/Vision for multimodal sentiment analysis.
- Upserts SocialMediaPost and ALERTS into SQLAlchemy DB.
- Deduplicates posts & alerts by UID.

Requirements:
  pip install playwright aiohttp sqlalchemy openai
  playwright install   # to install browser engines

Notes:
 - Provide env vars: OPENAI_API_KEY, DATABASE_URL (SQLAlchemy connection), optionally CHROME_USER_DATA_DIR.
 - You can use CHROME_USER_DATA_DIR to reuse logged-in profile and avoid manual login.
 - This script uses the new Responses/Vision style pattern. Adjust model names if needed.
 - Adjust CONCURRENCY to control parallelism.
"""

import os
import asyncio
import json
import re
import hashlib
from pathlib import Path
from datetime import datetime, timezone
from typing import List, Dict, Any, Optional
import aiohttp
import logging

from playwright.async_api import async_playwright, Page, BrowserContext
import sqlalchemy as sa
from sqlalchemy.orm import sessionmaker
# import OpenAI client (the 'openai' SDK or new client). We'll use "openai" package as most common.
import openai

# ---------------- CONFIG ----------------
OPENAI_API_KEY = os.getenv("OPENAI_API_KEY")
DATABASE_URL = os.getenv("DATABASE_URL", "sqlite:///linkedin_posts.db")
CHROME_USER_DATA_DIR = os.getenv("CHROME_USER_DATA_DIR")  # e.g. path to chrome profile to reuse login
COMPANY_SLUG = "udacity"   # change as needed
MAX_POSTS = 50             # number of recent posts to attempt
CONCURRENCY = 4            # parallel pages
DOWNLOAD_DIR = Path("downloaded_media")
HEADLESS = True
# Alert rules (tunable)
ALERT_KEYWORDS = ["lawsuit", "layoff", "fraud", "scam", "bankrupt", "data breach", "security breach"]
ALERT_NEGATIVE_SCORE_THRESHOLD = 0.75  # if negative and score >= threshold -> alert
# ----------------------------------------

logging.basicConfig(level=logging.INFO, format="%(asctime)s %(levelname)s %(message)s")
DOWNLOAD_DIR.mkdir(parents=True, exist_ok=True)

# ---------- DB: simple SQLAlchemy models ----------

metadata = sa.MetaData()

social_media_post = sa.Table(
    "social_media_post",
    metadata,
    sa.Column("id", sa.Integer, primary_key=True, index=True),
    sa.Column("uid", sa.String, unique=True, index=True),
    sa.Column("company_id", sa.Integer),
    sa.Column("post_platform", sa.String, default="linkedin"),
    sa.Column("post_url", sa.String),
    sa.Column("post_description", sa.Text),
    sa.Column("posted_at", sa.DateTime, default=datetime.utcnow),
    sa.Column("likes", sa.Integer, default=0),
    sa.Column("comments_count", sa.Integer, default=0),
    sa.Column("shares", sa.Integer, default=0),
    sa.Column("sentiment_label", sa.String),
    sa.Column("sentiment_score", sa.Float),
    sa.Column("media", sa.Text),  # JSON list of media paths/urls
    sa.Column("raw_json", sa.Text),
)

alerts_table = sa.Table(
    "alerts",
    metadata,
    sa.Column("alert_id", sa.Integer, primary_key=True),
    sa.Column("company_id", sa.Integer),
    sa.Column("alert_type", sa.String),
    sa.Column("severity", sa.String),
    sa.Column("source_channel", sa.String),
    sa.Column("detected_on", sa.DateTime),
    sa.Column("resolved", sa.Boolean, default=False),
    sa.Column("details", sa.Text),
    sa.Column("post_uid", sa.String, index=True),
)

engine = sa.create_engine(DATABASE_URL, echo=False, future=True)
metadata.create_all(engine)
SessionLocal = sessionmaker(bind=engine)

# ---------- OpenAI client ----------
if not OPENAI_API_KEY:
    raise RuntimeError("Set OPENAI_API_KEY environment variable.")
openai.api_key = OPENAI_API_KEY

# Helper: extract a UID from data-urn or link href (heuristic)
def extract_uid_from_element_info(data_urn: Optional[str], href: Optional[str]) -> Optional[str]:
    # LinkedIn URNs might look like: urn:li:activity:1234567890123456789
    if data_urn:
        m = re.search(r"activity:(\d+)", data_urn)
        if m:
            return m.group(1)
        # sometimes data-urn contains an encoded social URN
        m2 = re.search(r"urn:li:share:(\d+)", data_urn)
        if m2:
            return m2.group(1)
    if href:
        # match /activity/1234567890123456789 or /posts/123456...
        m = re.search(r"/activity/(\d+)", href)
        if m:
            return m.group(1)
        m2 = re.search(r"/posts/([^/?#]+)", href)
        if m2:
            return m2.group(1)
    return None

# ---------- OpenAI sentiment helpers ----------
async def openai_text_sentiment(text: str) -> Dict[str, Any]:
    """
    Classify sentiment for text into label, score(0..1), and reason.
    Uses the OpenAI Responses API with a structured response prompt (returns JSON).
    """
    # short prompt: ask for JSON output. You can replace model with latest multimodal if you have it.
    prompt = f"""
You are a sentiment analysis assistant. Given the following text, return a JSON object with keys:
- label: one of ["positive","neutral","negative","mixed"]
- score: a float from 0.0 to 1.0 representing confidence/severity (higher = stronger)
- reason: short explanation.

Text:
\"\"\"{text}\"\"\"
Return only valid JSON.
"""
    # Using OpenAI's "responses" endpoint style via openai.Completion fallback for compatibility.
    # If you have the newer SDK, swap for client.responses.create with input types including images.
    resp = openai.ChatCompletion.create(
        model="gpt-4o-mini",  # pick the LLM you have access to; adjust as needed
        messages=[{"role":"system","content":"You are a sentiment classifier."},
                  {"role":"user","content":prompt}],
        max_tokens=200,
        temperature=0.0,
    )
    # Parse assistant reply to JSON (best-effort)
    text_out = resp["choices"][0]["message"]["content"]
    try:
        # sometimes the assistant wraps JSON in ```; strip
        j = re.search(r"\{.*\}", text_out, flags=re.S)
        if j:
            return json.loads(j.group(0))
        return json.loads(text_out)
    except Exception:
        # fallback: simple heuristics
        label = "neutral"
        score = 0.5
        if "negative" in text_out.lower():
            label = "negative"
            score = 0.8
        elif "positive" in text_out.lower():
            label = "positive"
            score = 0.8
        return {"label": label, "score": score, "reason": text_out[:200]}

async def openai_image_and_text_sentiment(image_urls: List[str], text: str, comments_text: str) -> Dict[str, Any]:
    """
    Multimodal sentiment: provide image URLs + text + comments for a combined sentiment.
    Many OpenAI multimodal endpoints accept images; here we call the Responses API via a textual wrapper.
    If you have a real vision-enabled model in your OpenAI plan, replace the prompt + model accordingly.
    """
    # We will give the model the text and the image URLs and ask for combined sentiment.
    prompt = {
        "role": "user",
        "content": (
            "Analyze overall sentiment for the following LinkedIn post. "
            "Fields: post_text, comments_text (concatenate important comments), image_urls (list). "
            "Return JSON with: label, score (0-1), reasons (short) and flagged_terms (list)."
            f"\n\npost_text:\n{text}\n\ncomments_text:\n{comments_text}\n\nimage_urls:\n{json.dumps(image_urls)}\n\n"
            "Return only valid JSON."
        )
    }
    resp = openai.ChatCompletion.create(
        model="gpt-4o-mini",  # replace by your multimodal model if available, e.g. a vision-enabled "responses" model
        messages=[{"role":"system","content":"You are a multimodal sentiment classifier that can infer sentiment from text and images."}, prompt],
        max_tokens=300,
        temperature=0.0
    )
    content = resp["choices"][0]["message"]["content"]
    try:
        j = re.search(r"\{.*\}", content, flags=re.S)
        if j:
            return json.loads(j.group(0))
        return json.loads(content)
    except Exception:
        # fallback: text-only sentiment
        return await openai_text_sentiment(text)

# ---------- media download ----------
async def download_url(session: aiohttp.ClientSession, url: str, dest_dir: Path) -> Optional[str]:
    try:
        fname = hashlib.sha1(url.encode()).hexdigest()[:12]
        ext = os.path.splitext(url.split("?")[0])[1][:8] or ".bin"
        dest = dest_dir / f"{fname}{ext}"
        async with session.get(url, timeout=30) as r:
            if r.status == 200:
                content = await r.read()
                dest.write_bytes(content)
                return str(dest)
    except Exception as e:
        logging.warning("Failed to download %s: %s", url, e)
    return None

# ---------- alert rule ----------
def check_if_alert(company_id: int, uid: str, sentiment: Dict[str, Any], post_text: str, comments_text: str) -> Optional[Dict[str, Any]]:
    """
    Very simple rule-based alert:
    - If sentiment.label == 'negative' and score >= ALERT_NEGATIVE_SCORE_THRESHOLD
      OR any ALERT_KEYWORDS appear in post_text/comments_text -> create 'high' severity alert.
    """
    label = sentiment.get("label", "").lower()
    score = float(sentiment.get("score", 0) or 0)
    text_blob = (post_text or "") + " " + (comments_text or "")
    found_keywords = [kw for kw in ALERT_KEYWORDS if kw.lower() in text_blob.lower()]
    if (label == "negative" and score >= ALERT_NEGATIVE_SCORE_THRESHOLD) or found_keywords:
        severity = "high" if label == "negative" and score >= ALERT_NEGATIVE_SCORE_THRESHOLD else "medium"
        return {
            "company_id": company_id,
            "alert_type": "social_sentiment",
            "severity": severity,
            "source_channel": "linkedin",
            "detected_on": datetime.now(timezone.utc),
            "resolved": False,
            "details": json.dumps({"uid": uid, "label": label, "score": score, "keywords": found_keywords}),
            "post_uid": uid
        }
    return None

# ---------- Playwright crawling & processing ----------
async def process_post_item(context: BrowserContext, post_summary: Dict[str, Any], db_sess, semaphore: asyncio.Semaphore):
    """
    For a collected post summary (uid + link), open page, extract full text, media, comments, counts,
    run OpenAI sentiment, upsert DB, possibly create alert.
    """
    async with semaphore:
        uid = post_summary.get("uid")
        href = post_summary.get("href")
        logging.info("Processing UID=%s href=%s", uid, href)
        if not uid:
            logging.info("No uid present; skipping")
            return None

        page = await context.new_page()
        try:
            await page.goto(href, wait_until="domcontentloaded", timeout=30000)
        except Exception:
            # fallback: try opening the company feed and find post anchor then click (skip here for brevity)
            logging.warning("Failed to open post href, skipping: %s", href)
            await page.close()
            return None

        # Wait for article block
        try:
            await page.wait_for_selector("div[role='article']", timeout=5000)
        except Exception:
            pass

        # Extract full text
        try:
            post_block = await page.query_selector("div[role='article']")
            post_text = ""
            if post_block:
                # try common text containers
                txts = []
                for sel in [
                    "div.feed-shared-update__description",
                    "div.feed-shared-text",
                    "div.update-components-text",
                    "p"
                ]:
                    nodes = await post_block.query_selector_all(sel)
                    for n in nodes:
                        t = (await n.inner_text()).strip()
                        if t:
                            txts.append(t)
                    if txts:
                        break
                if not txts:
                    post_text = (await post_block.inner_text()).strip()
                else:
                    post_text = "\n\n".join(dict.fromkeys(txts))
            else:
                post_text = ""
        except Exception:
            post_text = ""

        # Extract reactions / shares / comments count heuristics
        likes = 0; shares = 0; comments_count = 0
        try:
            # look for elements that contain 'reactions' or number patterns
            text_all = await page.content()
            # quick regex search for common patterns (best-effort)
            m_like = re.search(r"([\d,\.]+)\s+(?:reactions|likes|reactions)", text_all, flags=re.I)
            if m_like:
                likes = int(m_like.group(1).replace(",",""))
            m_share = re.search(r"([\d,\.]+)\s+(?:shares|reposts)", text_all, flags=re.I)
            if m_share:
                shares = int(m_share.group(1).replace(",",""))
            m_comment = re.search(r"([\d,\.]+)\s+(?:comments|replies)", text_all, flags=re.I)
            if m_comment:
                comments_count = int(m_comment.group(1).replace(",",""))
        except Exception:
            pass

        # Extract image urls and pdf links inside post area
        image_urls = []
        pdf_urls = []
        try:
            if post_block:
                imgs = await post_block.query_selector_all("img")
                for img in imgs:
                    src = await img.get_attribute("src")
                    if src and src.startswith("http"):
                        image_urls.append(src)
                anchors = await post_block.query_selector_all("a")
                for a in anchors:
                    href_a = await a.get_attribute("href")
                    if href_a and href_a.lower().endswith(".pdf"):
                        pdf_urls.append(href_a)
                    # sometimes PDFs open in viewer - look for 'pdf' string
                    if href_a and "pdf" in href_a.lower() and href_a.startswith("http"):
                        pdf_urls.append(href_a)
        except Exception:
            pass

        # Extract comment threads (limit to some N)
        comments_texts = []
        try:
            # click "Show comments" buttons if present to load them (best-effort)
            try:
                btn = await page.query_selector("button[aria-label*='comments'], button:has-text('comments'), a:has-text('comments')")
                if btn:
                    try:
                        await btn.click()
                        await page.wait_for_timeout(400)
                    except Exception:
                        pass
            except Exception:
                pass
            # now collect comment blocks inside article
            comment_nodes = await page.query_selector_all("div.comments-comment-item, div.comments-comment, div[class*='comment']")
            for c in comment_nodes[:30]:
                text_c = (await c.inner_text()).strip()
                if text_c:
                    comments_texts.append(text_c)
        except Exception:
            pass

        # Download media (images & pdfs) concurrently using aiohttp
        downloaded_media = []
        async with aiohttp.ClientSession() as sess:
            tasks = []
            for url in set(image_urls + pdf_urls):
                tasks.append(asyncio.create_task(download_url(sess, url, DOWNLOAD_DIR)))
            results = await asyncio.gather(*tasks, return_exceptions=True)
            for r in results:
                if isinstance(r, str) and r:
                    downloaded_media.append(r)

        # Combine comments into single text chunk for sentiment analysis
        comments_blob = "\n".join(comments_texts[:20])

        # Run multimodal sentiment: images + text + comments
        try:
            sentiment = await openai_image_and_text_sentiment(image_urls, post_text, comments_blob)
        except Exception as e:
            logging.warning("OpenAI call failed: %s", e)
            sentiment = await openai_text_sentiment(post_text)

        # Upsert post into DB (dedupe by UID)
        with SessionLocal() as session:
            # check existing by uid
            existing = session.execute(sa.select(social_media_post).where(social_media_post.c.uid == uid)).first()
            media_json = json.dumps({"downloaded": downloaded_media, "image_urls": image_urls, "pdfs": pdf_urls})
            if existing:
                # update
                upd = social_media_post.update().where(social_media_post.c.uid == uid).values(
                    post_url=href,
                    post_description=post_text,
                    posted_at=datetime.utcnow(),
                    likes=likes,
                    comments_count=comments_count,
                    shares=shares,
                    sentiment_label=sentiment.get("label"),
                    sentiment_score=float(sentiment.get("score") or 0),
                    media=media_json,
                    raw_json=json.dumps(post_summary)
                )
                session.execute(upd)
                session.commit()
                logging.info("Updated post uid=%s", uid)
            else:
                ins = social_media_post.insert().values(
                    uid=uid,
                    company_id=0,  # fill accordingly
                    post_platform="linkedin",
                    post_url=href,
                    post_description=post_text,
                    posted_at=datetime.utcnow(),
                    likes=likes,
                    comments_count=comments_count,
                    shares=shares,
                    sentiment_label=sentiment.get("label"),
                    sentiment_score=float(sentiment.get("score") or 0),
                    media=media_json,
                    raw_json=json.dumps(post_summary)
                )
                session.execute(ins)
                session.commit()
                logging.info("Inserted post uid=%s", uid)

            # Create alert if rule matches and not duplicate for same post
            alert_obj = check_if_alert(0, uid, sentiment, post_text, comments_blob)
            if alert_obj:
                # dedupe by post_uid and company_id
                existing_alert = session.execute(
                    sa.select(alerts_table).where(
                        alerts_table.c.post_uid == uid
                    )
                ).first()
                if not existing_alert:
                    session.execute(alerts_table.insert().values(**alert_obj))
                    session.commit()
                    logging.warning("ALERT created for uid=%s: %s", uid, alert_obj["severity"])

        await page.close()
        return {"uid": uid, "sentiment": sentiment, "media": downloaded_media}

async def crawl_company_posts(company_slug: str):
    results = []
    semaphore = asyncio.Semaphore(CONCURRENCY)
    async with async_playwright() as p:
        browser = await p.chromium.launch(headless=HEADLESS, args=["--no-sandbox"])
        # persistent context uses CHROME_USER_DATA_DIR to reuse login
        context_args = {}
        if CHROME_USER_DATA_DIR:
            context_args["user_data_dir"] = CHROME_USER_DATA_DIR
        context = await browser.new_context(**context_args)
        page = await context.new_page()

        # Block some resources to speed up (analytics, fonts), but allow images & PDFs
        async def route_handler(route, request):
            url = request.url
            if any(x in url for x in ("google-analytics", "doubleclick", "facebook.net", "linkedin.com/px", "analytics")):
                await route.abort()
                return
            if request.resource_type in ("font", "stylesheet"):
                # stylesheet may be necessary for some layouts; but blocking speeds things up
                await route.abort()
                return
            await route.continue_()
        await context.route("**/*", route_handler)

        # Navigate to company posts page
        posts_url = f"https://www.linkedin.com/company/{company_slug}/posts/"
        await page.goto(posts_url, wait_until="domcontentloaded", timeout=30000)
        logging.info("Opened %s", posts_url)

        # Attempt to select 'Recent' filter if present (heuristic)
        try:
            # find text 'Sort by' -> click -> click 'Recent' option
            btn = await page.query_selector("button:has-text('Sort by'), button:has-text('Recent'), button[aria-label*='Sort']")
            if btn:
                try:
                    await btn.click()
                    await page.wait_for_timeout(300)
                    opt = await page.query_selector("button:has-text('Recent'), text=Recent")
                    if opt:
                        await opt.click()
                        logging.info("Selected Recent filter")
                except Exception:
                    pass
        except Exception:
            pass

        # Scroll and collect article elements until we collect enough UIDs
        collected = []
        seen_uids = set()
        # use a loop to scroll and collect
        scroll_tries = 0
        while len(collected) < MAX_POSTS and scroll_tries < 60:
            articles = await page.query_selector_all("div[role='article']")
            for a in articles:
                # try to extract data-urn or href
                data_urn = await a.get_attribute("data-urn")
                # try to find post href inside
                href_el = await a.query_selector("a[href*='/activity/'], a[href*='/posts/']")
                href = (await href_el.get_attribute("href")) if href_el else None
                uid = extract_uid_from_element_info(data_urn, href)
                if not uid:
                    # try to find any anchor and parse for urns
                    all_a = await a.query_selector_all("a[href]")
                    for aa in all_a:
                        ah = await aa.get_attribute("href")
                        uid = extract_uid_from_element_info(None, ah)
                        if uid:
                            href = ah
                            break
                if uid and uid not in seen_uids:
                    seen_uids.add(uid)
                    # capture a compact summary for processing
                    snippet = (await a.inner_text())[:300] if a else ""
                    collected.append({"uid": uid, "href": href or posts_url, "snippet": snippet})
                    logging.info("Collected uid=%s (total=%d)", uid, len(collected))
                    if len(collected) >= MAX_POSTS:
                        break
            # scroll further
            await page.evaluate("window.scrollBy(0, window.innerHeight);")
            await page.wait_for_timeout(700)  # small pause
            scroll_tries += 1

        logging.info("Collected %d posts to process", len(collected))

        # Process posts concurrently
        tasks = []
        for item in collected:
            tasks.append(process_post_item(context, item, SessionLocal(), semaphore))
        processed = await asyncio.gather(*tasks, return_exceptions=True)
        for p in processed:
            if isinstance(p, dict):
                results.append(p)

        await context.close()
        await browser.close()
    return results

import asyncio

def run_crawl_sync():
    """
    Run crawl_company_posts safely whether an event loop is already running (e.g. Jupyter)
    or not. Uses nest_asyncio when necessary.
    """
    try:
        loop = asyncio.get_event_loop()
    except RuntimeError:
        loop = None

    if loop and loop.is_running():
        # We're inside Jupyter / another running loop — allow nested loop execution
        try:
            import nest_asyncio
        except Exception:
            raise RuntimeError("Please install nest_asyncio in this environment: pip install nest_asyncio")
        nest_asyncio.apply()
        # run coroutine in the running loop
        result = loop.run_until_complete(crawl_company_posts(COMPANY_SLUG))
    else:
        # no running loop — safe to use asyncio.run
        result = asyncio.run(crawl_company_posts(COMPANY_SLUG))

    # persist results same as before
    with open("crawl_results.json", "w", encoding="utf-8") as f:
        import json
        json.dump(result, f, ensure_ascii=False, indent=2)
    print("Crawl finished. Saved crawl_results.json")
    return result

if __name__ == "__main__":
    run_crawl_sync()

NotImplementedError: 

In [4]:
# In a notebook cell
results = await crawl_company_posts(COMPANY_SLUG)


NotImplementedError: 